# IMSNG_Rougine.ipynb
- Automatically Process the image data from GECKO facilities and search for transients in the subtracted images with `gpPy`
- Author: Gregory S.H. Paek (23.04.24)

## Library

In [1]:
from __future__ import print_function, division, absolute_import
import os, sys, glob, subprocess
import numpy as np
import astropy.io.ascii as ascii
import matplotlib.pyplot as plt
plt.ioff()
from astropy.nddata import CCDData
from preprocess import calib
from util import tool
from astropy.io import fits
from astropy.table import Table, vstack
from astropy import units as u
from ccdproc import ImageFileCollection
import warnings
warnings.filterwarnings(action='ignore')
# from itertools import product
from itertools import repeat
import multiprocessing
import time
start_localtime = time.strftime('%Y-%m-%d %H:%M:%S (%Z)', time.localtime())

In [2]:
#	plot setting
import matplotlib.pyplot as plt
import matplotlib as mpl
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "last_expr"

mpl.rcParams["axes.titlesize"] = 14
mpl.rcParams["axes.labelsize"] = 20
plt.rcParams['savefig.dpi'] = 500
plt.rc('font', family='serif')

## Ready

In [3]:
# try:
# 	obs = (sys.argv[1]).upper()
# except:
# 	obs = input(f"OBS TO PROCESS:").upper()

obs = 'LOAO'
print(f'# Observatory : {obs.upper()}')

try:
	ncores = int(sys.argv[2])
except:
	ncores = 8
print(f"- Number of Cores: {ncores}")

# Observatory : LOAO
- Number of Cores: 8


### Path

In [4]:
path_base = '/data4/gecko/factory'
path_ref = f'{path_base}/ref_frames/{obs.upper()}'
path_factory = f'{path_base}/{obs.lower()}'
path_save = f'/data6/bkgdata/{obs.upper()}'
path_log = f'/home/paek/log/{obs.lower()}.log'
path_keys = '/home/paek/table'
#------------------------------------------------------------
path_gal = '/data6/IMSNG/IMSNGgalaxies'
path_refcat = '/data4/gecko/factory/ref_frames/LOAO'
#------------------------------------------------------------
path_config = '/home/paek/config'
path_default_gphot = f'/home/paek/config/gphot.{obs.lower()}.config'
# path_mframe = f'{path_base}/master_frames'
path_mframe = f'/data3/paek/factory/master_frames'
path_calib = f'{path_base}/calib'
#------------------------------------------------------------
#	Codes
#------------------------------------------------------------
path_phot_sg = './phot/gregoryphot_2021.py'
path_phot_mp = './phot/gregoryphot_mp_2021.py'
path_phot_sub = './phot/gregoryphot_sub_2021.py'
path_find = './phot/gregoryfind_bulk_mp_2021.py'
#------------------------------------------------------------
if 'KCT_ASI1600MM' in obs:
	path_raw = '/data3/IMSNG/KCT/obsdata'
else:
	path_raw = f'/data6/obsdata/{obs.upper()}'
rawlist = sorted(glob.glob(path_raw+'/2*'))
#------------------------------------------------------------
path_obs = '/home/paek/table/obs.dat'
path_changehdr = '/home/paek/table/changehdr.dat'
path_alltarget = '/home/paek/table/alltarget.dat'
ccdinfo = tool.getccdinfo(obs, path_obs)

- Folder setting

In [5]:
if not os.path.exists(path_base):
	os.makedirs(path_base)
if not os.path.exists(path_ref):
	os.makedirs(path_ref)
if not os.path.exists(path_factory):
	os.makedirs(path_factory)
if not os.path.exists(path_save):
	os.makedirs(path_save)

### Table

In [6]:
logtbl = ascii.read(path_log)
datalist = np.copy(logtbl['date'])
obstbl = ascii.read(path_obs)
hdrtbl = ascii.read(path_changehdr)
alltbl = ascii.read(path_alltarget)
keytbl = ascii.read(f'{path_keys}/keys.dat')

## Process Summary Status

In [7]:
protbl = Table()
protbl['process'] = ['master_frame', 'pre_process', 'astrometry', 'cr_removal', 'defringe', 'photometry', 'image_stack', 'photometry_com', 'subtraction', 'photometry_sub', 'transient_search', 'total']
protbl['status'] = False
protbl['time'] = 0.0 * u.second

## Main Body

In [8]:
newlist = [i for i in rawlist if (i not in datalist) & (i+'/' not in datalist)]
if len(newlist) == 0:
	print('No new data')
	sys.exit()
else:
	print(newlist)

# path = newlist[0]
path = "/data6/obsdata/LOAO/2023_0420"
tdict = dict()
starttime = time.time()
path_data = '{}/{}'.format(path_factory, os.path.basename(path))
#	Remove old folder and re-copy folder
rmcom = 'rm -rf {}'.format(path_data)
print(rmcom)
os.system(rmcom)
cpcom = 'cp -r {} {}'.format(path, path_data)
print(cpcom)
os.system(cpcom)

['/data6/obsdata/LOAO/2023_0424']
rm -rf /data4/gecko/factory/loao/2023_0420
cp -r /data6/obsdata/LOAO/2023_0420 /data4/gecko/factory/loao/2023_0420


0

### Header Correction

In [9]:
ic0 = ImageFileCollection(path_data, keywords='*')
ic0.summary.write('{}/hdr.raw.dat'.format(path_data), format='ascii.tab', overwrite=True) 
#	Exceptions
#	DOAO CCD
if obs == 'DOAO':
	instrume = ic0.summary['instrume'][0]
	if instrume == 'Apogee USB/Net':obs = 'DOAO_APOGEE'
	elif instrume == '':			obs = 'DOAO_FLI'
	elif instrume == 'FLI':			obs = 'DOAO_FLI'
	elif instrume == 'Moravian C4-16000':		obs = 'DOAO_C416K'
else:
	pass
obsinfo = calib.getobsinfo(obs, obstbl)
if obs == 'SAO_C361K':
	xbinning = ic0.summary['xbinning'][0]
	if xbinning > 1:
		print(f'{obs} : BINNINGx{xbinning}')
		obsinfo['pixscale'] = obsinfo['pixscale']*xbinning
	if ic0.summary['instrume'][0] == 'ASCOM Camera Driver for FLI Kepler':
		obsinfo['pixscale'] = 0.311
		obsinfo['fov'] = 0.25*60.
		obsinfo['gain'] = float(ic0.summary['egain'][0])
#	KHAO Binning
if obs == 'KHAO':
	xbinning = ic0.summary['xbinning'][0]
	if xbinning > 1:
		obsinfo['pixscale'] = obsinfo['pixscale']*2
#	LOAO
if obs == 'LOAO':
	instrume = ic0.summary['instrume'][0]
	if 'Finger Lakes' in instrume:
		obs = 'LOAO_FLI'
		obsinfo = calib.getobsinfo(obs, obstbl)
#	RASA Mode
if obs == 'RASA36':
	if 'hdr' in path:
		mode = 'hdr'
		badmode = True
	elif 'high' in path:
		mode = 'high'
		badmode = True
	else:
		mode = 'high'
		badmode = True
		pass
	print(f'Master Frame Mode:{mode} [Bad Mode:{badmode}]')

calib.correcthdr_routine(path_data, hdrtbl, obs)
print("Correction Done")
# objfilterlist, objexptimelist, flatfilterlist, darkexptimelist, obstime = calib.correcthdr_routine(path_data, hdrtbl)
ic1 = ImageFileCollection(path_data, keywords='*')
ic1.summary.write('{}/hdr.cor.dat'.format(path_data), format='ascii.tab', overwrite=True)
try:
	nobj = len(ic1.filter(imagetyp='OBJECT').summary)
except:
	nobj = len(ic1.filter(imagetyp='object').summary)	

------------------------------------------------------------
CHANGE TO UNIVERSAL HEADER SERIES ...
------------------------------------------------------------

/data4/gecko/factory/loao/2023_0420/dark.2x2.200.20230420.0011.fits
/data4/gecko/factory/loao/2023_0420/dark.2x2.200.20230420.0012.fits
/data4/gecko/factory/loao/2023_0420/dark.2x2.200.20230420.0013.fits
/data4/gecko/factory/loao/2023_0420/dark.2x2.200.20230420.0014.fits
/data4/gecko/factory/loao/2023_0420/dark.2x2.200.20230421.0015.fits
/data4/gecko/factory/loao/2023_0420/dark.2x2.200.20230421.0016.fits
/data4/gecko/factory/loao/2023_0420/dark.2x2.200.20230421.0017.fits
/data4/gecko/factory/loao/2023_0420/dark.2x2.200.20230421.0018.fits
/data4/gecko/factory/loao/2023_0420/dark.2x2.200.20230421.0019.fits
/data4/gecko/factory/loao/2023_0420/dark.2x2.200.20230421.0020.fits
/data4/gecko/factory/loao/2023_0420/dark.2x2.200.20230421.1089.fits
/data4/gecko/factory/loao/2023_0420/dark.2x2.200.20230421.1090.fits
/data4/gecko/factory/lo

### Marking the `GECKO` data

In [10]:
# testobj = 'S190425z'
project = "IMSNG"
obsmode = "MONITORING" # Default
for obj in ic1.filter(imagetyp='object').summary['object']:
	if 'MS' in obj[:2]: # MS230425 (test event)
		print(obj)
		project = "GECKO"
		obsmode = "TEST"
	elif 'S2' in obj[:2]: # S230425 (super event)
		print(obj)
		project = "GECKO"
		obsmode = "FOLLOWUP" # Follow-up
	else:
		pass
print(f"[{project}] {obsmode}")

[IMSNG] MONITORING


- Slack notification

In [11]:
OAuth_Token = keytbl['key'][keytbl['name']=='slack'].item()

channel = '#pipeline'
text = f'[`gpPy`/{project}-{obsmode}] Start Processing {obs} {os.path.basename(path)} Data ({nobj} objects) with {ncores} cores'

param_slack = dict(
	token = OAuth_Token,
	channel = channel,
	text = text,
)

tool.slack_bot(**param_slack)

<Response [200]>


### Master Frame

- Bias

In [12]:
st = time.time()
#------------------------------------------------------------
#	BIAS
#------------------------------------------------------------
try:
	biasnumb = len(ic1.filter(imagetyp='Bias').summary)
except:
	biasnumb = 0
# if len(ic1.filter(imagetyp='Bias').summary) != 0:
if biasnumb != 0:
	mzero = calib.master_zero(ic1, fig=False)
	# print(zeroim)
	date = fits.getheader(f'{path_data}/zero.fits')['date-obs'][:10].replace('-', '')
	if obs == 'RASA36':
		zeroim = f'{path_mframe}/{obs}/zero/{date}-zero_{mode}.fits'
	else:
		zeroim = f'{path_mframe}/{obs}/zero/{date}-zero.fits'
	cpcom = f'cp {path_data}/zero.fits {zeroim}'
	print(cpcom)
	os.system(cpcom)
	plt.close('all')
else:
	#	IF THERE IS NO FLAT FRAMES, BORROW FROM CLOSEST OTHER DATE
	print('\nNO BIAS FRAMES\n')
	if obs == 'RASA36':
		pastzero = np.array(glob.glob(f'{path_mframe}/{obs}/zero/*zero_{mode}.fits'))
	else:
		pastzero = np.array(glob.glob(f'{path_mframe}/{obs}/zero/*zero.fits'))
	#	CALCULATE CLOSEST ONE FROM TIME DIFFERENCE
	deltime = []
	for date in pastzero:
		zeromjd = calib.isot_to_mjd((os.path.basename(date)).split('-')[0])
		deltime.append(np.abs(ic1.summary['mjd'][0]-zeromjd))
	indx_closet = np.where(deltime == np.min(deltime))
	# tmpzero = path_data+'/'+os.path.basename(np.asscalar(pastzero[indx_closet]))
	tmpzero = f"{path_data}/{os.path.basename(pastzero[indx_closet][0])}"
	# cpcom = 'cp {} {}'.format(np.asscalar(pastzero[indx_closet]), tmpzero)
	cpcom = f'cp {pastzero[indx_closet][0]} {tmpzero}'
	print(cpcom)
	os.system(cpcom)
	# if obs != 'KCT':
	if 'KCT_ASI1600MM' in obs:
		#KCT Exception
		mzero = CCDData.read(tmpzero, hdu=0, unit='adu')
	elif obs == 'RASA36':
		if (mode == 'high') & (badmode == True):
			mzero = CCDData.read(tmpzero, hdu=0).multiply(20)
			print('[Bad mode] Multiply 20 on the high mode bias.')
		else:
			mzero = CCDData.read(tmpzero, hdu=0)
	elif obs == 'LSGT':
		mzero = CCDData.read(tmpzero, hdu=0, unit='adu')
	else:
		mzero = CCDData.read(tmpzero, hdu=0)#, unit='adu')
	mzero.meta['FILENAME'] = os.path.basename(tmpzero)

------------------------------------------------------------
MAKING MASTER ZERO
------------------------------------------------------------

20 ZERO IMAGES WILL BE COMBINED.
cp /data4/gecko/factory/loao/2023_0420/zero.fits /data3/paek/factory/master_frames/LOAO/zero/20230421-zero.fits


- Dark

In [13]:
#------------------------------------------------------------
#	DARK (ITERATION FOR EACH EXPOSURE TIMES)
#------------------------------------------------------------
try:
	darkexptimelist = sorted(list(set(ic1.filter(imagetyp='dark').summary['exptime'])))
	darknumb = len(darkexptimelist)
except:
	darknumb = 0
darkdict = dict()
# if len(darkexptimelist) != 0:
if darknumb != 0:
	dark_process = True
	for i, exptime in enumerate(darkexptimelist):
		print('PRE PROCESS FOR DARK ({} sec)\t[{}/{}]'.format(exptime, i+1, len(darkexptimelist)))
		mdark = calib.master_dark(ic1, mzero=mzero, exptime=exptime, fig=False)
		darkdict['{}'.format(int(exptime))] = mdark

		date = fits.getheader(f'{path_data}/dark-{int(exptime)}.fits')['date-obs'][:10].replace('-', '')
		if obs == 'RASA36':
			darkim = f'{path_mframe}/{obs}/dark/{int(exptime)}-{date}-dark_{mode}.fits'
		else:
			darkim = f'{path_mframe}/{obs}/dark/{int(exptime)}-{date}-dark.fits'
		# print(zeroim)
		cpcom = 'cp {}/dark-{}.fits {}'.format(path_data, int(exptime), darkim)
		print(cpcom)
		os.system(cpcom)
		plt.close('all')
else:
	#	Borrow
	print('\nNO DARK FRAMES\n')
	objexptimelist = sorted(list(set(ic1.filter(imagetyp='object').summary['exptime'])))
	exptime = objexptimelist[-1]
	# pastdark = np.array(glob.glob('{}/{}/dark/{}*dark*.fits'.format(path_mframe, obs, int(exptime))))
	if obs == 'RASA36':
		pastdark = np.array(glob.glob(f'{path_mframe}/{obs}/dark/{int(exptime)}*dark_{mode}.fits'))
	else:
		pastdark = np.array(glob.glob(f'{path_mframe}/{obs}/dark/{int(exptime)}*dark.fits'))

	if len(pastdark) == 0:
		pastdark = np.array(glob.glob('{}/{}/dark/*dark*.fits'.format(path_mframe, obs)))
	else:
		pass
	#	CALCULATE CLOSEST ONE FROM TIME DIFFERENCE
	deltime = []
	delexptime = []
	darkexptimes = []
	for date in pastdark:
		# darkmjd = calib.isot_to_mjd((os.path.basename(date)).split('-')[0])
		darkmjd = calib.isot_to_mjd((os.path.basename(date)).split('-')[1])
		darkexptime = int( os.path.basename(date).split('-')[0] )
		# darkexptime = delexptime.append(int( os.path.basename(date).split('-')[1] ))
		darkexptimes.append(darkexptime)
		deltime.append(np.abs(ic1.summary['mjd'][0]-darkmjd))
	if 'KCT' in obs:
		indx_closet = np.where(
			(np.abs(np.array(darkexptimes)-exptime) == np.min(np.abs(np.array(darkexptimes)-exptime)))
		)
	else:
		indx_closet = np.where(
			(deltime == np.min(deltime)) &
			(darkexptimes == np.max(darkexptimes))
		)
	if len(indx_closet[0]) == 0:
		indx_closet = np.where(
			(deltime == np.min(deltime))
		)
	else:
		pass
	# tmpdark = path_data+'/'+os.path.basename(pastdark[indx_closet].item())
	# tmpdark = '{}/{}'.format(path_data, os.path.basename(pastdark[indx_closet[0]].item()))
	# tmpdark = pastdark[indx_closet[0]].item()
	tmpdark = pastdark[indx_closet][-1]
	exptime = int(fits.getheader(tmpdark)['exptime'])

	# cpcom = 'cp {} {}/dark-{}.fits'.format(tmpdark, path_data, int(exptime))
	cpcom = 'cp {} {}'.format(tmpdark, path_data, int(exptime))
	print(cpcom)
	os.system(cpcom)
	if 'KCT' in obs:
		#KCT Exception
		mdark = CCDData.read(tmpdark, hdu=0, unit='adu')
	elif obs == 'RASA36':
		if (mode == 'high') & (badmode == True):
			mdark = CCDData.read(tmpdark, hdu=0).multiply(20)
			print('[Bad mode] Multiply 20 on the high mode dark.')
		else:
			mdark = CCDData.read(tmpdark, hdu=0)
	elif obs == 'LSGT':
		mdark = CCDData.read(tmpdark, hdu=0, unit='adu')
	else:
		mdark = CCDData.read(tmpdark, hdu=0)#, unit='adu')
	mdark.meta['FILENAME'] = os.path.basename(tmpdark)
	mdark.meta['EXPTIME'] = exptime
	darkdict['{}'.format(int(exptime))] = mdark

PRE PROCESS FOR DARK (200.0 sec)	[1/1]
------------------------------------------------------------
MAKING MASTER DARK
------------------------------------------------------------

cp /data4/gecko/factory/loao/2023_0420/dark-200.fits /data3/paek/factory/master_frames/LOAO/dark/200-20230421-dark.fits


- Flat

In [14]:
flatdict = dict()
try:
	flatfilterlist = list(set(ic1.filter(imagetyp='flat').summary['filter']))
	for i, filte in enumerate(flatfilterlist):
		# print(i, filte)
		print('MAKING MASTER FLAT IN {}-BAND'.format(filte))
		mflat = calib.master_flat(ic1, mzero, filte, mdark=mdark, fig=True)
		flatdict[filte] = mflat

		date = fits.getheader(f'{path_data}/dark-{int(exptime)}.fits')['date-obs'][:10].replace('-', '')
		if obs == 'RASA36':
			flatim = f'{path_mframe}/{obs}/flat/{date}-n{filte}_{mode}.fits'
		else:
			flatim = f'{path_mframe}/{obs}/flat/{date}-n{filte}.fits'
		cpcom = f'cp {path_data}/n{filte}.fits {flatim}'
		print(cpcom)
		os.system(cpcom)
		plt.close('all')
except:
	print('No flat calibration image.')
	# flatdict['None'] = None
	pass
# tdict['masterframe'] = time.time() - st
protbl['status'][protbl['process']=='master_frame'] = True
protbl['time'][protbl['process']=='master_frame'] = int(time.time() - st)
#------------------------------------------------------------
#	OBJECT CALIBARTION (ZERO, DARK, FLAT)
#------------------------------------------------------------
st_ = time.time()
comment     = '='*60+'\n' \
			+ 'OBJECT CALIBRATION\n' \
			+ '='*60+'\n'
print(comment)
objfilterlist = sorted(list(set(ic1.filter(imagetyp='object').summary['filter'])))
objexptimelist = sorted(list(set(ic1.filter(imagetyp='object').summary['exptime'])))
for i, filte in enumerate(objfilterlist):
	print('PRE PROCESS FOR {} FILTER OBJECT\t[{}/{}]'.format(filte, i+1, len(objfilterlist)))
	if filte in flatdict.keys():
		mflat = flatdict[filte]
	else:
		print('\nNO {} FLAT FRAMES\n'.format(filte))
		#	CALCULATE CLOSEST ONE FROM TIME DIFFERENCE
		deltime = []
		if obs != 'RASA36':
			pastflat = np.array(glob.glob('{}/{}/flat/*n{}*.fits'.format(path_mframe, obs, filte)))
			for date in pastflat:
				flatmjd = calib.isot_to_mjd((os.path.basename(date)).split('-')[0])
				deltime.append(np.abs(ic1.summary['mjd'][0]-flatmjd))
		elif obs == 'RASA36':
			pastflat = np.array(glob.glob(f'{path_mframe}/{obs}/flat/*_{mode}-n{filte}*.fits'))
			for date in pastflat:
				flatmjd = fits.getheader(date)['MJD']
				deltime.append(np.abs(ic1.summary['mjd'][0]-flatmjd))

		indx_closet = np.where(deltime == np.min(deltime))
		tmpflat = '{}/{}'.format(path_data, os.path.basename(pastflat[indx_closet][0].item()))
		# tmpflat = pastflat[indx_closet][0].item()
		cpcom = 'cp {} {}'.format(pastflat[indx_closet][0].item(), tmpflat)
		print(cpcom)
		os.system(cpcom)
		if ('KCT' not in obs) & (obs != 'LSGT'):
			mflat = CCDData.read(tmpflat, hdu=0)#, unit='adu')
		elif obs == 'LSGT':
			mflat = CCDData.read(tmpflat, hdu=0, unit='adu')
		else:
			#KCT Exception
			mflat = CCDData.read(tmpflat, hdu=0, unit='adu')
			mflat.meta['FILENAME'] = os.path.basename(tmpflat)
		mflat.meta['FILENAME'] = os.path.basename(tmpflat)
		flatdict[filte] = mflat
	for expt in objexptimelist:
		if str(int(expt)) in darkdict.keys():
			mdark = darkdict[str(int(expt))]
		else:
			mdark = darkdict[list(darkdict.keys())[-1]]
		calib.calibration(ic1, mzero, mflat, filte, mdark=mdark)
# tdict['objectcorrection'] = time.time() - st - tdict[list(tdict.keys())[-1]]
protbl['status'][protbl['process']=='pre_process'] = True
protbl['time'][protbl['process']=='pre_process'] = int(time.time() - st_)
#	Corrected image list
fzimlist = []
for ims in ('{}/fz*.fits'.format(path_data), '{}/fz*.fit'.format(path_data), '{}/fz*.fts'.format(path_data)):
	fzimlist.extend(sorted(glob.glob(ims)))

MAKING MASTER FLAT IN B-BAND
------------------------------------------------------------
MAKING MASTER FLAT
------------------------------------------------------------

SUBTRACT MASTER ZERO & DARK FROM B FLAT
10 B FLAT IMAGES WILL BE COMBINED.
cp /data4/gecko/factory/loao/2023_0420/nB.fits /data3/paek/factory/master_frames/LOAO/flat/20230421-nB.fits
MAKING MASTER FLAT IN V-BAND
------------------------------------------------------------
MAKING MASTER FLAT
------------------------------------------------------------

SUBTRACT MASTER ZERO & DARK FROM V FLAT
10 V FLAT IMAGES WILL BE COMBINED.
cp /data4/gecko/factory/loao/2023_0420/nV.fits /data3/paek/factory/master_frames/LOAO/flat/20230421-nV.fits
MAKING MASTER FLAT IN I-BAND
------------------------------------------------------------
MAKING MASTER FLAT
------------------------------------------------------------

SUBTRACT MASTER ZERO & DARK FROM I FLAT
14 I FLAT IMAGES WILL BE COMBINED.
cp /data4/gecko/factory/loao/2023_0420/nI.fits

### WCS Calculation

In [15]:
#------------------------------------------------------------
#	ASTROMETRY
#------------------------------------------------------------
st_ = time.time()
print('ASTROMETRY START')
print('='*60)
astrometryfailist = []
# fzimlist = sorted(glob.glob(path_data+'/fz*.fits'))
astimlist = []
astotlist = []
astralist = []
astdelist = []

for inim in fzimlist:
	obj = (fits.getheader(inim)['object']).upper()
	if (obj in alltbl['obj']):
		indx_target = np.where(obj == alltbl['obj'])[0][0]
		ra, dec = alltbl['ra'][indx_target].item(), alltbl['dec'][indx_target].item()
		astimlist.append(inim)
		astralist.append(ra)
		astdelist.append(dec)
	else:
		astotlist.append(inim)
#	Astrometry (IMSNG field)
if __name__ == '__main__':
	with multiprocessing.Pool(processes=ncores) as pool:
		results = pool.starmap(calib.astrometry, zip(astimlist, repeat(obsinfo['pixscale']), astralist, astdelist, repeat(obsinfo['fov']/60.), repeat(15)))
#	Astrometry (non IMSNG field)
if __name__ == '__main__':
	with multiprocessing.Pool(processes=ncores) as pool:
		results = pool.starmap(calib.astrometry, zip(astotlist, repeat(obsinfo['pixscale']), repeat(None), repeat(None), repeat(None), repeat(60)))
#	Astrometry (failed IMSNG field)
astfailist = []
for inim in astimlist:
	if (os.path.exists('{}/a{}'.format(path_data, os.path.basename(inim))) == False):
		astfailist.append(inim)
if __name__ == '__main__':
	with multiprocessing.Pool(processes=ncores) as pool:
		results = pool.starmap(calib.astrometry, zip(astfailist, repeat(obsinfo['pixscale']), repeat(None), repeat(None), repeat(None), repeat(60)))
for inim in astfailist:
	if (os.path.exists('{}/a{}'.format(path_data, os.path.basename(inim))) == False):
		astrometryfailist.append('{}/a{}'.format(path_data, os.path.basename(inim)))

os.system('rm '+path_data+'/*.axy '+path_data+'/*.corr '+path_data+'/*.xyls '+path_data+'/*.match '+path_data+'/*.rdls '+path_data+'/*.solved '+path_data+'/*.wcs ')
print('ASTROMETRY COMPLETE\n'+'='*60)
# tdict['astronomy'] = time.time() - st - tdict[list(tdict.keys())[-1]]
protbl['status'][protbl['process']=='astrometry'] = True
protbl['time'][protbl['process']=='astrometry'] = int(time.time() - st_)

ASTROMETRY START
/usr/local/astrometry/bin/solve-field /data4/gecko/factory/loao/2023_0420/fzobj.NGC5668.20230421.1035.fits --scale-unit arcsecperpix --scale-low 0.7146 --scale-high 0.8734000000000001 --no-plots --new-fits /data4/gecko/factory/loao/2023_0420/afzobj.NGC5668.20230421.1035.fits --overwrite --use-sextractor --cpulimit 15 --ra 14:33:24.300 --dec +04:27:01.19 --radius 0.4683333333333334/usr/local/astrometry/bin/solve-field /data4/gecko/factory/loao/2023_0420/fzobj.NGC5850.20230421.1029.fits --scale-unit arcsecperpix --scale-low 0.7146 --scale-high 0.8734000000000001 --no-plots --new-fits /data4/gecko/factory/loao/2023_0420/afzobj.NGC5850.20230421.1029.fits --overwrite --use-sextractor --cpulimit 15 --ra 15:07:07.644 --dec +01:32:40.74 --radius 0.4683333333333334/usr/local/astrometry/bin/solve-field /data4/gecko/factory/loao/2023_0420/fzobj.NGC5850.20230421.1031.fits --scale-unit arcsecperpix --scale-low 0.7146 --scale-high 0.8734000000000001 --no-plots --new-fits /data4/geck


> WARNING: default.sex not found, using internal defaults

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:38:03 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog

> WARNING: default.sex not found, using internal defaults

> Looking for fzobj.NGC5668.20230421.1035.fits

> WARNING: default.sex not found, using internal defaults

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:38:03 with 1 thread

> Setting catalog parameters
----- Measuring from: fzobj.NGC5668.20230421.1035.fits [0/3]
      "NGC5668" / no ext. header / 2048x2048 / 64 bits (floats)
Detection+Measurement image: > Setting up background maps
> Reading detection filter
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:38:03 with 1 thread

> Setting catalog parameters

> WARNING: default.sex not found, using internal defaults

> Reading detection filter
> Initializing catalog

> WARNING: default.sex not found, using internal defaults

> Initializing catalog
> 
--

Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writing row 0
Done
Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writing row 0
Done
Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writing row 0
Done
Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writing row 0
Done
Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writ


> WARNING: default.sex not found, using internal defaults

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:38:09 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for fzobj.NGC5668.20230421.1040.fits
----- Measuring from: fzobj.NGC5668.20230421.1040.fits [0/3]
      "NGC5668" / no ext. header / 2048x2048 / 64 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting

Field 1 did not solve (index index-4206-07.fits, field objects 1-10).
Field 1 did not solve (index index-4206-02.fits, field objects 1-10).
Field 1 did not solve (index index-4206-02.fits, field objects 1-10).
Field 1 did not solve (index index-4206-02.fits, field objects 1-10).
Field 1 did not solve (index index-4206-02.fits, field objects 1-10).
Field 1 did not solve (index index-4206-02.fits, field objects 1-10).
Field 1 did not solve (index index-4205-07.fits, field objects 1-10).
Field 1 did not solve (index index-4205-07.fits, field objects 1-10).


...

Extracting sources...
Reading file "/data4/gecko/factory/loao/2023_0420/fzobj.NGC6555.20230421.1052.axy"...
Only searching for solutions within 0.468333 degrees of RA,Dec (271.955,17.6049)
Field 1 did not solve (index index-4209.fits, field objects 1-10).
Field 1 did not solve (index index-4208.fits, field objects 1-10).
Field 1 did not solve (index index-4207-07.fits, field objects 1-10).
  log-odds ratio 182.095 (1.21004e+79), 23 match, 0 conflict, 25 distractors, 27 index.
  RA,Dec = (271.955,17.603), pixel scale 0.794559 arcsec/pix.
  Hit/miss:   Hit/miss: +-+++-+-+-++++--+--++--+---+++-+---+--+++------+(best)----------------------------------------------------


> Line: 1225  Objects:        0 detected /        0 sextracted
> Line: 1250  Objects:        0 detected /        0 sextracted
> Line: 1275  Objects:        0 detected /        0 sextracted
> Line: 1300  Objects:        0 detected /        0 sextracted
> Line:   75  Objects:      125 detected /        0 sextracted
> Line: 1325  Objects:        0 detected /        0 sextracted
> Line: 1350  Objects:        0 detected /        0 sextracted
> Line: 1375  Objects:        0 detected /        0 sextracted
> Line: 1400  Objects:        0 detected /        0 sextracted
> Line:  100  Objects:      170 detected /        0 sextracted
> Line: 1425  Objects:        0 detected /        0 sextracted
> Line: 1450  Objects:        0 detected /        0 sextracted
> Line: 1475  Objects:        0 detected /        0 sextracted
> Line: 1500  Objects:        0 detected /        0 sextracted
> Line:  125  Objects:      213 detected /        0 sextracted
> Line: 1525  Objects:        0 detected /        0 sex

Field 1: solved with index index-4206-07.fits.
Field 1 solved: writing to file /data4/gecko/factory/loao/2023_0420/fzobj.NGC6555.20230421.1052.solved to indicate this.
Field: /data4/gecko/factory/loao/2023_0420/fzobj.NGC6555.20230421.1052.fits
Field center: (RA,Dec) = (271.955108, 17.602808) deg.
Field center: (RA H:M:S, Dec D:M:S) = (18:07:49.226, +17:36:10.107).
Field size: 27.1141 x 27.1248 arcminutes
Field rotation angle: up is -176.142 degrees E of N
Field parity: pos
Creating new FITS file "/data4/gecko/factory/loao/2023_0420/afzobj.NGC6555.20230421.1052.fits"...



> Line:  175  Objects:      387 detected /        0 sextracted
> Line:  200  Objects:      411 detected /        0 sextracted
> Line:  225  Objects:      449 detected /        0 sextracted
> Line: 1575  Objects:     2163 detected /      785 sextracted
> Line:  250  Objects:      480 detected /        0 sextracted
> Line: 1585  Objects:     2181 detected /      800 sextracted
> Line:  275  Objects:      505 detected /        0 sextracted
> Line:  300  Objects:      537 detected /        0 sextracted
> Line: 1600  Objects:     2201 detected /      819 sextracted
> Line:  325  Objects:      566 detected /        0 sextracted
> Line:  350  Objects:      591 detected /        0 sextracted
> Line:  375  Objects:      615 detected /        0 sextracted
> Line:  400  Objects:      637 detected /        0 sextracted
> Line:  425  Objects:      667 detected /        0 sextracted
> Line: 1625  Objects:     2248 detected /      853 sextracted
> Line:  450  Objects:      683 detected /        0 sex

Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writing row 0
Done
Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writing row 0
Done
Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writing row 0
Done
Solving...
Solving...
Solving...
Reading file "/data4/gecko/factory/loao/2023_0420/fzobj.NGC6814.20230421.1054.axy"...
Only searching for solutions within 0.468333 degrees of RA,Dec (295.669,-10.3237)
Field 1 did not solve (index index-4209.fits, field objects 1-10).
Field 1 did not solve (index index-4208.fits, field objects 1-10).
Field 1 did not solve (index index-4207-07.fits, field o

### Cosmic-ray Removal

In [16]:
st_ = time.time()
print('Quick seeing measurement with SE & Cosmic ray removal')
print('='*60)
gain = ccdinfo['gain'].value
rdnoise = ccdinfo['rdnoise']

# afzimlist = sorted(glob.glob(path_data+'/afz*.fits'))
afzimlist = []
for ims in ('{}/a*.fits'.format(path_data), '{}/a*.fit'.format(path_data), '{}/a*.fts'.format(path_data)):
	afzimlist.extend(sorted(glob.glob(ims)))
outimlist = []
for i, inim in enumerate(afzimlist):
	outim = '{}/cr{}'.format(os.path.dirname(inim), os.path.basename(inim))
	outimlist.append(outim)
if ('KCT' not in obs) & ('RASA36' not in obs) & ('LOAO_FLI' not in obs):
	#	Seeing measurement
	if __name__ == '__main__':
		with multiprocessing.Pool(processes=ncores) as pool:
			results = pool.starmap(tool.SE_seeing, zip(afzimlist, repeat(obs), repeat(path_obs), repeat(path_config), repeat(3*u.arcsecond), repeat(0.95), repeat(True)))
	#	Remove cosmic-ray
	if __name__ == '__main__':
		with multiprocessing.Pool(processes=ncores) as pool:
			results = pool.starmap(calib.cr_removal, zip(afzimlist, outimlist, repeat(gain), repeat(rdnoise)))
else:
	print('Skip Seeing measurement & CR remove processes for {}'.format(obs))
	for inim, outim in zip(afzimlist, outimlist):
		cpcom = 'cp {} {}'.format(inim, outim)
		print(cpcom)
		os.system(cpcom)
protbl['status'][protbl['process']=='cr_removal'] = True
protbl['time'][protbl['process']=='cr_removal'] = int(time.time() - st_)

Quick seeing measurement with SE & Cosmic ray removal


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:38:31 with 1 thread

> 
> Setting catalog parameters
----- SExtractor 2.19.5 started on 2023-04-26 at 15:38:31 with 1 thread

> Setting catalog parameters
> 
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:38:31 with 1 thread

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:38:31 with 1 thread

----- SExtractor 2.19.5 started on 2023-04-26 at 15:38:31 with 1 thread

> Setting catalog parameters
> Setting catalog parameters
> Setting catalog parameters
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:38:31 with 1 thread

> Setting catalog parameters
> 
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:38:31 with 1 thread

----- SExtractor 2.19.5 started on 2023-04-26 at 15:38:31 with 1 thread

> Setting catalog parameters
> Setting catalog parameters
> Reading detection filter
> Reading detection filter
> Reading detection filter
> Reading detection filter
> Initializing Neural Network
> Reading Neural Netwo

Remove 767 cosmic-ray for /data4/gecko/factory/loao/2023_0420/afzobj.NGC5850.20230421.1029.fits [8.535 sec]
Remove 776 cosmic-ray for /data4/gecko/factory/loao/2023_0420/afzobj.NGC5850.20230421.1033.fits [8.542 sec]
Remove 754 cosmic-ray for /data4/gecko/factory/loao/2023_0420/afzobj.NGC5668.20230421.1037.fits [8.569 sec]
Remove 760 cosmic-ray for /data4/gecko/factory/loao/2023_0420/afzobj.NGC5962.20230421.1025.fits [8.619 sec]
Remove 860 cosmic-ray for /data4/gecko/factory/loao/2023_0420/afzobj.NGC5668.20230421.1039.fits [8.659 sec]
Remove 727 cosmic-ray for /data4/gecko/factory/loao/2023_0420/afzobj.NGC5962.20230421.1023.fits [8.925 sec]
Remove 705 cosmic-ray for /data4/gecko/factory/loao/2023_0420/afzobj.NGC5850.20230421.1031.fits [8.956 sec]
Remove 733 cosmic-ray for /data4/gecko/factory/loao/2023_0420/afzobj.NGC5668.20230421.1035.fits [9.312 sec]
Remove 655 cosmic-ray for /data4/gecko/factory/loao/2023_0420/afzobj.NGC5850.20230421.1034.fits [8.036 sec]
Remove 781 cosmic-ray for /d

### Rename to IMSNG/GECKO Convention

In [17]:
fov = obsinfo['fov']*u.arcmin 
crafzimlist = []
for ims in ('{}/cra*.fits'.format(path_data), '{}/cra*.fit'.format(path_data), '{}/cra*.fts'.format(path_data)):
	crafzimlist.extend(sorted(glob.glob(ims)))
# for inim in sorted(glob.glob('{}/crafz*.fits'.format(path_data))): 
for inim in crafzimlist:
	obj = fits.getheader(inim)['object'] 
	#	Modify incorrect object header
	if (inim.replace('crafz', 'afz') in astrometryfailist) & (obj in alltbl['obj']): 
		robj, sep = tool_tbd.imsng_name_correction(inim, alltbl, radius=fov) 
	else:
		pass
	calib.fnamechange(inim, obs)

caliblist = sorted(glob.glob(path_data+'/Calib*.fits'))
ic_cal = ImageFileCollection(path_data, glob_include='Calib*0.fits', keywords='*')
os.system('chmod 777 {}'.format(path_data))
os.system('chmod 777 {}/*'.format(path_data))
#	Calib-*.fits TO SAVE PATH
f = open(path_data+'/object.txt', 'a')
f.write('obs obj dateobs filter exptime\n')
for inim in caliblist:
	img = os.path.basename(inim)
	part = img.split('-')
	line = '{} {} {} {} {}\n'.format(part[1], part[2], part[3]+'T'+part[4], part[5], part[6])
	print(line)
	f.write(line)
f.close()

#	DATA FOLDER TO SAVE PATH
# os.system('rm {}/afz*.fits {}/fz*.fits'.format(path_data, path_data))
os.system(f'rm {path_data}/*fz*.f*')
os.system(f'rm -rf {path_save}/{os.path.basename(path_data)}')
plt.close('all')

mv /data4/gecko/factory/loao/2023_0420/crafzobj.NGC5668.20230421.1035.fits /data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112336-B-60.fits
mv /data4/gecko/factory/loao/2023_0420/crafzobj.NGC5668.20230421.1036.fits /data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112453-B-60.fits
mv /data4/gecko/factory/loao/2023_0420/crafzobj.NGC5668.20230421.1037.fits /data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112610-B-60.fits
mv /data4/gecko/factory/loao/2023_0420/crafzobj.NGC5668.20230421.1038.fits /data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112730-R-60.fits
mv /data4/gecko/factory/loao/2023_0420/crafzobj.NGC5668.20230421.1039.fits /data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112848-R-60.fits
mv /data4/gecko/factory/loao/2023_0420/crafzobj.NGC5668.20230421.1040.fits /data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-113005-R-60.fits
mv /data4/gecko/factory/loao/2023_0420/crafzobj.NGC5850.20230421

In [18]:
for calibim in caliblist:

	center, vertices = tool.get_wcs_coordinates(calibim)

	fits.setval(calibim, "RACENT", value=round(center[0].item(), 3), comment="RA CENTER [deg]")	
	fits.setval(calibim, "DECCENT", value=round(center[1].item(), 3), comment="DEC CENTER [deg]")	
	
	for ii, (_ra, _dec) in enumerate(vertices):
		# print(ii, _ra, _dec)
		fits.setval(calibim, f"RAPOLY{ii}", value=round(_ra, 3), comment=f"RA POLYGON {ii} [deg]")	
		fits.setval(calibim, f"DEPOLY{ii}", value=round(_dec, 3), comment=f"DEC POLYGON {ii} [deg]")
		

### Defringe
- Only for LOAO z, I, Y-bands

In [19]:
st_ = time.time()
if (obs == 'LOAO') & ('I' in ic_cal.filter(imagetyp='object').summary['filter']):
	dfim = '/home/paek/qsopy/fringe/LOAO/fringe_i_ori.fits'
	dfdat = '/home/paek/qsopy/fringe/LOAO/fringe_i.dat'
	dfimlist = []
	for inim in ic_cal.filter(imagetyp='object', filter='I').summary['file']:
		# dfimlist.append(calib.defringe(str(inim), dfim, dfdat))
		dfedim = calib.defringe(str(inim), dfim, dfdat)
		mvcom = 'mv {} {}'.format(dfedim, inim)
		print(mvcom)
		os.system(mvcom)
	# tdict['defringe'] = time.time() - st - tdict[list(tdict.keys())[-1]]
else:
	print('No images to defringe')
	pass
protbl['status'][protbl['process']=='defringe'] = True
protbl['time'][protbl['process']=='defringe'] = int(time.time() - st_)
#------------------------------------------------------------
print('='*60)
print('Calibration IS DONE.\t('+str(int(time.time() - starttime))+' sec)')
print('='*60)

No images to defringe
Calibration IS DONE.	(350 sec)


## Photometry

In [20]:
st_ = time.time()
print('#\tPhotometry')
path_infile = f'{path_data}/{os.path.basename(path_default_gphot)}'
path_new_gphot = f'{os.path.dirname(path_infile)}/gphot.config'

#	Copy default photometry configuration
cpcom = f'cp {path_default_gphot} {path_new_gphot}'
print(cpcom)
os.system(cpcom)

#	Read default photometry configuration
f = open(path_default_gphot, 'r')
lines = f.read().splitlines()
f.close()

#	Write photometry configuration
g = open(path_new_gphot, 'w')
for line in lines:
	if 'imkey' in line:
		line = f'imkey\t{path_data}/C*0.fits'
	else:
		pass
	g.write(line+'\n')
g.close()

if obs == 'DOAO':
	path_phot = path_phot_sg
else:
	path_phot = path_phot_mp

#	Execute
com = f'python {path_phot} {path_data} {ncores}'
# com = f'python {path_phot} {path_data} 1'
print(com)
os.system(com)

protbl['status'][protbl['process']=='photometry'] = True
protbl['time'][protbl['process']=='photometry'] = int(time.time() - st_)

#	Photometry
cp /home/paek/config/gphot.loao.config /data4/gecko/factory/loao/2023_0420/gphot.config
python ./phot/gregoryphot_mp_2021.py /data4/gecko/factory/loao/2023_0420 8
/data4/gecko/factory/loao/2023_0420/gphot.config
No transient catalog for photometry
#	42 images to do photometry
0	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112336-B-60.fits
1	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112453-B-60.fits
2	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112610-B-60.fits
3	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112730-R-60.fits
4	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112848-R-60.fits
5	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-113005-R-60.fits
6	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5850-20230421-111254-B-60.fits
7	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5850-20230421-111413-B-60.fits
8	/data4/gecko/factory/loao/2023_0420/Calib-LO

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:39:37 with 1 thread

> Setting catalog parameters

> WARNING: Not enough apertures provided in config.:
         some APER photometric values will remain blank 

> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights

> WARNING: Not enough apertures provided in config.:
         some APER photometric values will remain blank 

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:39:37 with 1 thread

> Setting catalog parameters
> Initializing catalog

> WARNING: Not enough apertures provided in config.:
         some APER photometric values will remain blank 

> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Looking for Calib-LOAO-NGC5850-20230421-111254-B-60.fits

> WARNING: Not enough apertures provided in config.:
         some APER photometric values will remain blank 

> Initializing catalog
> Looking for Calib-LOAO-NGC5668-20230421-112336-B-60.fit

2. SOURCE EXTRACTOR
2. SOURCE EXTRACTOR
3. MATCHING
3. MATCHING
2. SOURCE EXTRACTOR
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 57
--------------------------------------------------
FLAG(<=2)				: 56
B REF. MAGCUT (12.0-20.0)		: 57
Berr REF. MAGERR CUT < 0.05		: 57
MAGERR_AUTO CUT < 0.05		: 28
TOTAL #					: 27
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 56
--------------------------------------------------
FLAG(<=2)				: 55
B REF. MAGCUT (12.0-20.0)		: 56
Berr REF. MAGERR CUT < 0.05		: 56
MAGERR_AUTO CUT < 0.05		: 27
TOTAL #					: 26
2. SOURCE EXTRACTOR
2. SOURCE EXTRACTOR
2. SOURCE EXTRACTOR
2. SOURCE EXTRACTOR
3. MATCHING
3. MATCHING
3. MATCHING
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 106
--------------------------------------------------
FLAG(<=2)				: 105
B REF. MAGCUT (12.0-20.0)		: 106
Berr RE

MAG TYP     : MAG_AUTO
ZP          = 26.144
ZP ERR      = 0.035
STD.NUMB    = 46
REJ.NUMB    = 5
MAG TYP     : MAG_AUTO
ZP          = 26.028
ZP ERR      = 0.031
STD.NUMB    = 43
REJ.NUMB    = 15
CLIP UPPER  = 1
CLIP UPPER  = 7
CTIP LOWER  = 4
4-2. CHANGE HEADER
CTIP LOWER  = 8
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER [2/7]
--------------------------------------------------
ALL					: 112
--------------------------------------------------
FLAG(<=2)				: 112
B REF. MAGCUT (12.0-20.0)		: 112
Berr REF. MAGERR CUT < 0.05		: 111
MAGERR_APER CUT < 0.05		: 75
TOTAL #					: 75
FAIL TO DRAW ZEROPOINT GRAPH
4-2. CHANGE HEADER
FAIL TO DRAW ZEROPOINT GRAPH
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER [2/7]
--------------------------------------------------
ALL					: 115
--------------------------------------------------
FLAG(<=2)				: 113
R REF. MAGCUT (12.0-20.0)		: 115
Rerr REF. MAGERR CUT < 0.05		: 115
MAGERR_APER CUT < 0.0

MAG TYP     : MAG_APER_1
ZP          = 25.448
ZP ERR      = 0.037
STD.NUMB    = 30
REJ.NUMB    = 5
CLIP UPPER  = 3
CTIP LOWER  = 2
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_1 [3/7]
--------------------------------------------------
ALL					: 106
--------------------------------------------------
FLAG(<=2)				: 105
B REF. MAGCUT (12.0-20.0)		: 106
Berr REF. MAGERR CUT < 0.05		: 106
MAGERR_APER_1 CUT < 0.05		: 79
TOTAL #					: 78
==================================================4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]

--------------------------------------------------
ALL					: 56
--------------------------------------------------
FLAG(<=2)				: 55
B REF. MAGCUT (12.0-20.0)		: 56
Berr REF. MAGERR CUT < 0.05		: 56
MAGERR_APER_2 CUT < 0.05		: 33
TOTAL #					: 32
FAIL TO DRAW ZEROPOINT GRAPH
4-2. CHANGE HEADER
MAG TYP     : MAG_APER
ZP          = 25.616
ZP ERR      = 0.049
STD.NUMB    = 63
REJ.NUMB    = 12
CLIP UPPER  = 11


...

MAG TYP     : MAG_APER
ZP          = 25.726
ZP ERR      = 0.04
STD.NUMB    = 390
REJ.NUMB    = 54
CLIP UPPER  = 25
CTIP LOWER  = 29
4-1. PLOT
FAIL TO DRAW ZEROPOINT GRAPH
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_1 [3/7]
--------------------------------------------------
ALL					: 744
--------------------------------------------------
FLAG(<=2)				: 711
R REF. MAGCUT (12.0-20.0)		: 744
Rerr REF. MAGERR CUT < 0.05		: 744
MAGERR_APER_1 CUT < 0.05		: 469
TOTAL #					: 445


MAG TYP     : MAG_APER_1
ZP          = 25.665
ZP ERR      = 0.039
STD.NUMB    = 382
REJ.NUMB    = 63
CLIP UPPER  = 29
CTIP LOWER  = 34
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 744
--------------------------------------------------
FLAG(<=2)				: 711
R REF. MAGCUT (12.0-20.0)		: 744
Rerr REF. MAGERR CUT < 0.05		: 744
MAGERR_APER_2 CUT < 0.05		: 443
TOTAL #					: 419
MAG TYP     : MAG_APER_2
ZP          = 25.991
ZP ERR      = 0.039
STD.NUMB    = 364
REJ.NUMB    = 55
CLIP UPPER  = 33
CTIP LOWER  = 22
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_3 [5/7]
--------------------------------------------------
ALL					: 744
--------------------------------------------------
FLAG(<=2)				: 711
R REF. MAGCUT (12.0-20.0)		: 744
Rerr REF. MAGERR CUT < 0.05		: 744
MAGERR_APER_3 CUT < 0.05		: 358
TOTAL #					: 340
MAG TYP     : MAG_APER_3
ZP          = 26.141
ZP

4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 1173
--------------------------------------------------
FLAG(<=2)				: 1114
R REF. MAGCUT (12.0-20.0)		: 1173
Rerr REF. MAGERR CUT < 0.05		: 1173
MAGERR_AUTO CUT < 0.05		: 578
TOTAL #					: 533
MAG TYP     : MAG_AUTO
ZP          = 26.181
ZP ERR      = 0.028
STD.NUMB    = 358
REJ.NUMB    = 175
CLIP UPPER  = 96
CTIP LOWER  = 79
4-2. CHANGE HEADER
MAG TYP     : MAG_APER_1
ZP          = 25.666
ZP ERR      = 0.037
STD.NUMB    = 324
REJ.NUMB    = 52
CLIP UPPER  = 27
CTIP LOWER  = 25
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 639
--------------------------------------------------
FLAG(<=2)				: 619
R REF. MAGCUT (12.0-20.0)		: 639
Rerr REF. MAGERR CUT < 0.05		: 639
MAGERR_APER_2 CUT < 0.05		: 365
TOTAL #					: 350
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER [2/7]
----

4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_1 [3/7]
--------------------------------------------------
ALL					: 1173
--------------------------------------------------
FLAG(<=2)				: 1114
R REF. MAGCUT (12.0-20.0)		: 1173
Rerr REF. MAGERR CUT < 0.05		: 1173
MAGERR_APER_1 CUT < 0.05		: 759
TOTAL #					: 709
MAG TYP     : MAG_APER_3
ZP          = 26.147
ZP ERR      = 0.036
STD.NUMB    = 234
REJ.NUMB    = 54
CLIP UPPER  = 33
CTIP LOWER  = 21
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_4 [6/7]
--------------------------------------------------
ALL					: 639
--------------------------------------------------
FLAG(<=2)				: 619
R REF. MAGCUT (12.0-20.0)		: 639
Rerr REF. MAGERR CUT < 0.05		: 639
MAGERR_APER_4 CUT < 0.05		: 365
TOTAL #					: 352
MAG TYP     : MAG_APER_1
ZP          = 25.682
ZP ERR      = 0.046
STD.NUMB    = 623
REJ.NUMB    = 86
CLIP UPPER  = 35
CTIP LOWER  = 51
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULAT

MAG TYP     : MAG_APER_1
ZP          = 25.644
ZP ERR      = 0.049
STD.NUMB    = 586
REJ.NUMB    = 61
CLIP UPPER  = 22
CTIP LOWER  = 39
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 1106
--------------------------------------------------
FLAG(<=2)				: 1051
R REF. MAGCUT (12.0-20.0)		: 1106
Rerr REF. MAGERR CUT < 0.05		: 1106
MAGERR_APER_2 CUT < 0.05		: 664
TOTAL #					: 617
MAG TYP     : MAG_APER_2
ZP          = 25.979
ZP ERR      = 0.039
STD.NUMB    = 531
REJ.NUMB    = 86
CLIP UPPER  = 44
CTIP LOWER  = 42
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_3 [5/7]
--------------------------------------------------
ALL					: 1106
--------------------------------------------------
FLAG(<=2)				: 1051
R REF. MAGCUT (12.0-20.0)		: 1106
Rerr REF. MAGERR CUT < 0.05		: 1106
MAGERR_APER_3 CUT < 0.05		: 563
TOTAL #					: 520
MAG TYP     : MAG_APER_3
ZP          = 2

## Image registering & combine

In [21]:
st_ = time.time()
print('IMAGE REGISTERING & COMBINE')
combined_images = []
step = (1/24/60)*60	# 1 hour
ic_cal_phot = ImageFileCollection(path_data, glob_include='Calib*0.fits', keywords='*')
calist = sorted(glob.glob('{}/Calib*.fits'.format(path_data)))
objlist = sorted(list(set(ic_cal_phot.summary['object'])))
filterlist = sorted(list(set(ic_cal_phot.summary['filter'])))
# obj = 'NGC3147'
# filte = 'R'
for obj in objlist:
	for filte in filterlist:
		imlist_tmp = sorted(glob.glob('{}/Calib*-{}-*-{}-*.fits'.format(path_data, obj, filte)))
		if len(imlist_tmp) == 0:
			pass
		elif len(imlist_tmp) == 1:
			inim = imlist_tmp[0]
			comim = inim.replace('.fits', '.com.fits')
			cpcom = f'cp {inim} {comim}'
			print(cpcom)
			os.system(cpcom)
		else:
			print(obj, filte)
			# ic_part = sorted(glob.glob('{}/Calib*{}*{}*.fits'.format(path_data, obj, filte)))

			jds = np.array([fits.getheader(inim)['jd'] for inim in imlist_tmp])
			delts = jds - np.min(jds)

			grouplist = []
			grouplists = []

			i = 0
			for i in range(len(delts)):
				#	Initial setting
				if i == 0:
					t0 = delts[i]
				#	Add last group to grouplists
				elif i == len(delts)-1:
					grouplists.append(grouplist)
				t1 = delts[i]
				# print(t0, t1)
				dif = np.abs(t0-t1)

				if dif < step:
					grouplist.append(imlist_tmp[i])
				#	Generate new group
				else:
					grouplists.append(grouplist)
					grouplist = [imlist_tmp[i]]	 
				t0 = t1
				
			for group in grouplists:
				print('-'*60)
				if len(group) > 1:
					ref_image = group[0]
					images_to_align = group[1:]
					for inim in group:
						print(inim)
					# _data, _hdr = fits.getdata(ref_image, header=True)
					# ximage, yimage = _data.shape
					# racent, decent = _hdr['RACENT'], _hdr['DECCENT']
					try:
						# outim = tool.swarpcomb(
						# 	images_to_align,
						# 	gain=obsinfo['gain'].value,
						# 	pixscale=obsinfo['pixscale'],
						# 	racent=racent,
						# 	decent=decent,
						# 	ximage=ximage,
						# 	yimage=yimage,
						# 	listname='obj.list',
						# 	path_save='.',
						# 	keys_to_get=[
						# 		'OBJECT',
						# 		'FILTER',
						# 		'RACENT',
						# 		'DECCENT',
						# 		'RAPOLY0',
						# 		'DEPOLY0',
						# 		'RAPOLY1',
						# 		'DEPOLY1',
						# 		'RAPOLY2',
						# 		'DEPOLY2',
						# 		'RAPOLY3',
						# 		'DEPOLY3',
						# 		]
						# 	)
						outim = tool.imcombine_routine(images_to_align, ref_image)
						combined_images.append(outim)
					except:
						print('Fail to image align & combine routine.')
						print(images_to_align)
						pass
				else:
					print('There is only one image.')
					combined_images.append(group[0])

protbl['status'][protbl['process']=='image_stack'] = True
protbl['time'][protbl['process']=='image_stack'] = int(time.time() - st_)

IMAGE REGISTERING & COMBINE
NGC5668 B
------------------------------------------------------------
/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112336-B-60.fits
/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112453-B-60.fits
/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112610-B-60.fits


Reference image	: /data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112336-B-60.fits
Input images	:
/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112453-B-60.fits
/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112610-B-60.fits
#	IMAGE REGISTERING
##########  Preparing reference ...
No filter file found, using default filter
No NNW file found, using default NNW config


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:41:03 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC5668-20230421-112336-B-60.fits
----- Measuring from: Calib-LOAO-NGC5668-20230421-112336-B-60.fits
      "NGC5668" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 164
EXT_NUMBER values found in catalog : 1
I've selected 152 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  152 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
########## Processing /data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112453-B-60.fits
No filter file found, using default filter
No NNW file found, using default NNW config


> Setting up background map at line: 1024
> Setting up background map at line: 1088
> Setting up background map at line: 1152
> Setting up background map at line: 1216
> Setting up background map at line: 1280
> Setting up background map at line: 1344
> Setting up background map at line: 1408
> Setting up background map at line: 1472
> Setting up background map at line: 1536
> Setting up background map at line: 1600
> Setting up background map at line: 1664
> Setting up background map at line: 1728
> Setting up background map at line: 1792
> Setting up background map at line: 1856
> Setting up background map at line: 1920
> Setting up background map at line: 1984
> Filtering background map(s)
> Computing background d-map
> Computing background-noise d-map
(M+D) Background: 222.784    RMS: 8.89431    / Threshold: 26.6829    
> Scanning image
> Line:   25  Objects:       11 detected /        0 sextracted
> Line:   50  Objects:       15 detected /        0 sextracted
> Line:   75  Objects

...

Number of sources in catalog : 1614
EXT_NUMBER values found in catalog : 1
I've selected 1564 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
########## Processing /data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC6814-20230421-115802-R-60.fits
No filter file found, using default filter
No NNW file found, using default NNW config


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:41:56 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC6814-20230421-115802-R-60.fits
----- Measuring from: Calib-LOAO-NGC6814-20230421-115802-R-60.fits
      "NGC6814" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 1581
EXT_NUMBER values found in catalog : 1
I've selected 1532 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00005414) : Rotation   -0.002168 [deg], scale 1.000054
Cand  2 (dist.   0.00005591) : Rotation   +0.000545 [deg], scale 1.000030
Cand  3 (dist.   0.00007612) : Rotation   +0.000545 [deg], scale 1.000030
Cand  4 (dist.   0.00009287) : Rotation   +0.000545 [deg], scale 1.000030
487/500 stars with distance < r = 5.0 (mean 0.1, median 0.1, std 0.1)
Filtered for companions, keeping 487/487 matches
Refitting transform (before/after) :
Rotation   -0.002168 [deg], scale 1.000054
Rotation   -0.000102 [deg], scale 1.000044
487/500 stars with distance < r = 5.0 (mean 0.1, median 0.1, std 0.1)
Filtered for companions, keeping 487/487 matches
I'm done !
Computed flux ratio fro

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:41:56 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC6814-20230421-115919-R-60.fits
----- Measuring from: Calib-LOAO-NGC6814-20230421-115919-R-60.fits
      "NGC6814" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 1399
EXT_NUMBER values found in catalog : 1
I've selected 1358 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00003018) : Rotation   -0.000257 [deg], scale 1.000040
Cand  2 (dist.   0.00003290) : Rotation   +0.000882 [deg], scale 1.000033
Cand  3 (dist.   0.00003423) : Rotation   +0.000882 [deg], scale 1.000033
Cand  4 (dist.   0.00003855) : Rotation   +0.000882 [deg], scale 1.000033
488/500 stars with distance < r = 5.0 (mean 0.1, median 0.1, std 0.3)
Filtered for companions, keeping 488/488 matches
Refitting transform (before/after) :
Rotation   -0.000257 [deg], scale 1.000040
Rotation   +0.000172 [deg], scale 1.000043
488/500 stars with distance < r = 5.0 (mean 0.1, median 0.1, std 0.3)
Filtered for companions, keeping 488/488 matches
I'm done !
Computed flux ratio fro

In [22]:
images_to_align = group
ref_image = images_to_align[0]

outim = tool.imcombine_routine(images_to_align, ref_image)

Reference image	: /data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC6814-20230421-115645-R-60.fits
Input images	:
/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC6814-20230421-115645-R-60.fits
/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC6814-20230421-115802-R-60.fits
/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC6814-20230421-115919-R-60.fits
#	IMAGE REGISTERING
##########  Preparing reference ...
No filter file found, using default filter
No NNW file found, using default NNW config


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:42:00 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC6814-20230421-115645-R-60.fits
----- Measuring from: Calib-LOAO-NGC6814-20230421-115645-R-60.fits
      "NGC6814" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 1614
EXT_NUMBER values found in catalog : 1
I've selected 1564 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
########## Processing /data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC6814-20230421-115645-R-60.fits
No filter file found, using default filter
No NNW file found, using default NNW config


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:42:00 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC6814-20230421-115645-R-60.fits
----- Measuring from: Calib-LOAO-NGC6814-20230421-115645-R-60.fits
      "NGC6814" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 1614
EXT_NUMBER values found in catalog : 1
I've selected 1564 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00000000) : Rotation   -0.000000 [deg], scale 1.000000
Cand  2 (dist.   0.00000000) : Rotation   +0.000000 [deg], scale 1.000000
Cand  3 (dist.   0.00000000) : Rotation   -0.000000 [deg], scale 1.000000
Cand  4 (dist.   0.00000000) : Rotation   -0.000000 [deg], scale 1.000000
500/500 stars with distance < r = 5.0 (mean 0.0, median 0.0, std 0.0)
Filtered for companions, keeping 500/500 matches
Refitting transform (before/after) :
Rotation   -0.000000 [deg], scale 1.000000
Rotation   +0.000000 [deg], scale 1.000000
500/500 stars with distance < r = 5.0 (mean 0.0, median 0.0, std 0.0)
Filtered for companions, keeping 500/500 matches
I'm done !
Computed flux ratio fro

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:42:01 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC6814-20230421-115802-R-60.fits
----- Measuring from: Calib-LOAO-NGC6814-20230421-115802-R-60.fits
      "NGC6814" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 1581
EXT_NUMBER values found in catalog : 1
I've selected 1532 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00005414) : Rotation   -0.002168 [deg], scale 1.000054
Cand  2 (dist.   0.00005591) : Rotation   +0.000545 [deg], scale 1.000030
Cand  3 (dist.   0.00007612) : Rotation   +0.000545 [deg], scale 1.000030
Cand  4 (dist.   0.00009287) : Rotation   +0.000545 [deg], scale 1.000030
487/500 stars with distance < r = 5.0 (mean 0.1, median 0.1, std 0.1)
Filtered for companions, keeping 487/487 matches
Refitting transform (before/after) :
Rotation   -0.002168 [deg], scale 1.000054
Rotation   -0.000102 [deg], scale 1.000044
487/500 stars with distance < r = 5.0 (mean 0.1, median 0.1, std 0.1)
Filtered for companions, keeping 487/487 matches
I'm done !
Computed flux ratio fro

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:42:02 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC6814-20230421-115919-R-60.fits
----- Measuring from: Calib-LOAO-NGC6814-20230421-115919-R-60.fits
      "NGC6814" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 1399
EXT_NUMBER values found in catalog : 1
I've selected 1358 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00003018) : Rotation   -0.000257 [deg], scale 1.000040
Cand  2 (dist.   0.00003290) : Rotation   +0.000882 [deg], scale 1.000033
Cand  3 (dist.   0.00003423) : Rotation   +0.000882 [deg], scale 1.000033
Cand  4 (dist.   0.00003855) : Rotation   +0.000882 [deg], scale 1.000033
488/500 stars with distance < r = 5.0 (mean 0.1, median 0.1, std 0.3)
Filtered for companions, keeping 488/488 matches
Refitting transform (before/after) :
Rotation   -0.000257 [deg], scale 1.000040
Rotation   +0.000172 [deg], scale 1.000043
488/500 stars with distance < r = 5.0 (mean 0.1, median 0.1, std 0.3)
Filtered for companions, keeping 488/488 matches
I'm done !
Computed flux ratio fro

## Photometry for combined images

In [23]:
st_ = time.time()
#	Write photometry configuration
h = open(path_new_gphot, 'w')
for line in lines:
	if 'imkey' in line:
		line = '{}\t{}/C*com.fits'.format('imkey', path_data)
	else:
		pass
	h.write(line+'\n')
h.close()
#	Execute
path_phot = path_phot_mp
com = 'python {} {} {}'.format(path_phot, path_data, ncores)
print(com)
os.system(com)
# tdict['photometry_com'] = time.time() - st - tdict[list(tdict.keys())[-1]]
protbl['status'][protbl['process']=='photometry_com'] = True
protbl['time'][protbl['process']=='photometry_com'] = int(time.time() - st_)

ic_com_phot = ImageFileCollection(path_data, glob_include='Calib*com.fits', keywords='*')	
#	Summary
print('Draw observation summary plots')
# for filte in list(set(ic_cal_phot.summary['filter'])):
for filte in filterlist:
	try:
		tool.obs_summary(filte, ic_cal_phot, ic_com_phot, path_save=path_data)
	except:
		print('Fail to make summary plots.')
		pass
	plt.close('all')

python ./phot/gregoryphot_mp_2021.py /data4/gecko/factory/loao/2023_0420 8
/data4/gecko/factory/loao/2023_0420/gphot.config
No transient catalog for photometry
#	15 images to do photometry
0	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112526-B-180.com.fits
1	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5668-20230421-112819-R-180.com.fits
2	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5850-20230421-111355-B-180.com.fits
3	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5850-20230421-111814-R-180.com.fits
4	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5962-20230421-110224-B-180.com.fits
5	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC5962-20230421-110614-R-180.com.fits
6	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC6070-20230421-113404-B-180.com.fits
7	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC6070-20230421-113824-R-180.com.fits
8	/data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC6090-20230421-105052-B-180.com.fits
9	/data4/gecko/fact


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:42:09 with 1 thread

> Setting catalog parameters
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:42:09 with 1 thread

> Setting catalog parameters
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:42:09 with 1 thread

> Setting catalog parameters

> WARNING: Not enough apertures provided in config.:
         some APER photometric values will remain blank 

> Reading detection filter

> WARNING: Not enough apertures provided in config.:
         some APER photometric values will remain blank 

> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights

> WARNING: Not enough apertures provided in config.:
         some APER photometric values will remain blank 

> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing Neural Network
> Reading Neural Network Weights

> WARNING: Not enough apertures provided in config.:
         some APER photo

2. SOURCE EXTRACTOR
3. MATCHING
2. SOURCE EXTRACTOR
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 78
--------------------------------------------------
FLAG(<=2)				: 76
B REF. MAGCUT (12.0-20.0)		: 78
Berr REF. MAGERR CUT < 0.05		: 78
MAGERR_AUTO CUT < 0.05		: 38
TOTAL #					: 37
2. SOURCE EXTRACTOR
2. SOURCE EXTRACTOR
3. MATCHING
MAG TYP     : MAG_AUTO
ZP          = 25.911
ZP ERR      = 0.042
STD.NUMB    = 32
REJ.NUMB    = 5
CLIP UPPER  = 4
CTIP LOWER  = 1
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER [2/7]
--------------------------------------------------
ALL					: 78
--------------------------------------------------
FLAG(<=2)				: 76
B REF. MAGCUT (12.0-20.0)		: 78
Berr REF. MAGERR CUT < 0.05		: 78
MAGERR_APER CUT < 0.05		: 48
TOTAL #					: 46
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
3. MATCHING
--------------------------------------------------
ALL					: 123
------------------------

FAIL TO DRAW ZEROPOINT GRAPH
4-2. CHANGE HEADER
2. SOURCE EXTRACTOR
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_1 [3/7]
--------------------------------------------------
ALL					: 78
--------------------------------------------------
FLAG(<=2)				: 76
B REF. MAGCUT (12.0-20.0)		: 78
Berr REF. MAGERR CUT < 0.05		: 78
MAGERR_APER_1 CUT < 0.05		: 48
TOTAL #					: 46
2. SOURCE EXTRACTOR
MAG TYP     : MAG_AUTO
ZP          = 26.02
ZP ERR      = 0.044
STD.NUMB    = 65
REJ.NUMB    = 15
CLIP UPPER  = 11
CTIP LOWER  = 4
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER [2/7]
--------------------------------------------------
ALL					: 123
--------------------------------------------------
FLAG(<=2)				: 122
B REF. MAGCUT (12.0-20.0)		: 123
Berr REF. MAGERR CUT < 0.05		: 123
MAGERR_APER CUT < 0.05		: 89
TOTAL #					: 88
MAG TYP     : MAG_AUTO
ZP          = 25.959
ZP ERR      = 0.047
STD.NUMB    = 75
REJ.NUMB    = 11
CLIP UPPER  = 10
CTIP LOWER  = 1


FAIL TO DRAW ZEROPOINT GRAPH
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_1 [3/7]
--------------------------------------------------
ALL					: 123
--------------------------------------------------
FLAG(<=2)				: 122
B REF. MAGCUT (12.0-20.0)		: 123
Berr REF. MAGERR CUT < 0.05		: 123
MAGERR_APER_1 CUT < 0.05		: 89
TOTAL #					: 88
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 220
--------------------------------------------------
FLAG(<=2)				: 216
R REF. MAGCUT (12.0-20.0)		: 220
Rerr REF. MAGERR CUT < 0.05		: 220
MAGERR_AUTO CUT < 0.05		: 127
TOTAL #					: 122
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
MAG TYP     : MAG_APER
ZP          = 25.71
ZP ERR      = 0.048
STD.NUMB    = 83
REJ.NUMB    = 14
--------------------------------------------------
ALL					: 203
--------------------------------------------------
FLAG(<=2)				: 196
R REF. MAGCUT (12.0-20.0)		: 203
Rerr REF. MAGERR CUT < 0.0

...

MAG TYP     : MAG_APER_1
ZP          = 25.51
ZP ERR      = 0.043
STD.NUMB    = 205
REJ.NUMB    = 25
CLIP UPPER  = 18
CTIP LOWER  = 7
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 414
--------------------------------------------------
FLAG(<=2)				: 407
B REF. MAGCUT (12.0-20.0)		: 414
Berr REF. MAGERR CUT < 0.05		: 412
MAGERR_APER_2 CUT < 0.05		: 218
TOTAL #					: 211
MAG TYP     : MAG_APER_2
ZP          = 25.84
ZP ERR      = 0.036
STD.NUMB    = 178
REJ.NUMB    = 33
CLIP UPPER  = 18
CTIP LOWER  = 15
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_3 [5/7]
--------------------------------------------------
ALL					: 414
--------------------------------------------------
FLAG(<=2)				: 407
B REF. MAGCUT (12.0-20.0)		: 414
Berr REF. MAGERR CUT < 0.05		: 412
MAGERR_APER_3 CUT < 0.05		: 168
TOTAL #					: 161
MAG TYP     : MAG_APER_3
ZP          = 25.981
ZP ER

2. SOURCE EXTRACTOR
MAG TYP     : MAG_APER_1
ZP          = 25.54
ZP ERR      = 0.042
STD.NUMB    = 415
REJ.NUMB    = 56
CLIP UPPER  = 29
CTIP LOWER  = 27
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 837
--------------------------------------------------
FLAG(<=2)				: 808
B REF. MAGCUT (12.0-20.0)		: 837
Berr REF. MAGERR CUT < 0.05		: 837
MAGERR_APER_2 CUT < 0.05		: 481
TOTAL #					: 455
MAG TYP     : MAG_APER_2
ZP          = 25.873
ZP ERR      = 0.033
STD.NUMB    = 370
REJ.NUMB    = 85
CLIP UPPER  = 48
CTIP LOWER  = 37
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_3 [5/7]
--------------------------------------------------
ALL					: 837
--------------------------------------------------
FLAG(<=2)				: 808
B REF. MAGCUT (12.0-20.0)		: 837
Berr REF. MAGERR CUT < 0.05		: 837
MAGERR_APER_3 CUT < 0.05		: 394
TOTAL #					: 370
3. MATCHING
4. ZERO POINT CAL

MAG TYP     : MAG_APER_5
ZP          = 25.793
ZP ERR      = 0.036
STD.NUMB    = 396
REJ.NUMB    = 73
CLIP UPPER  = 44
CTIP LOWER  = 29
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
3. MATCHING
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 1015
--------------------------------------------------
FLAG(<=2)				: 960
R REF. MAGCUT (12.0-20.0)		: 1015
Rerr REF. MAGERR CUT < 0.05		: 1015
MAGERR_AUTO CUT < 0.05		: 495
TOTAL #					: 454
MAG TYP     : MAG_APER_1
ZP          = 25.66
ZP ERR      = 0.035
STD.NUMB    = 442
REJ.NUMB    = 106
CLIP UPPER  = 37
CTIP LOWER  = 69
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 933
--------------------------------------------------
FLAG(<=2)				: 885
R REF. MAGCUT (12.0-20.0)		: 933
Rerr REF. MAGERR CUT < 0.05		: 933
MAGERR_APER_2 CUT < 0.05		: 562
TOTAL #					: 519
MAG TYP     : MAG_AUTO
ZP          = 

FAIL TO DRAW ZEROPOINT GRAPH
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_1 [3/7]
--------------------------------------------------
ALL					: 1015
--------------------------------------------------
FLAG(<=2)				: 960
R REF. MAGCUT (12.0-20.0)		: 1015
Rerr REF. MAGERR CUT < 0.05		: 1015
MAGERR_APER_1 CUT < 0.05		: 645
TOTAL #					: 593
MAG TYP     : MAG_APER_3
ZP          = 26.13
ZP ERR      = 0.037
STD.NUMB    = 351
REJ.NUMB    = 84
CLIP UPPER  = 62
CTIP LOWER  = 22
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_4 [6/7]
--------------------------------------------------
ALL					: 933
--------------------------------------------------
FLAG(<=2)				: 885
R REF. MAGCUT (12.0-20.0)		: 933
Rerr REF. MAGERR CUT < 0.05		: 933
MAGERR_APER_4 CUT < 0.05		: 553
TOTAL #					: 514
MAG TYP     : MAG_APER_1
ZP          = 25.662
ZP ERR      = 0.037
STD.NUMB    = 496
REJ.NUMB    = 97
CLIP UPPER  = 41
CTIP LOWER  = 56
4-2. CHANGE HEADE

MAG TYP     : MAG_APER_1
ZP          = 25.658
ZP ERR      = 0.049
STD.NUMB    = 783
REJ.NUMB    = 76
CLIP UPPER  = 29
CTIP LOWER  = 47
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 1478
--------------------------------------------------
FLAG(<=2)				: 1349
R REF. MAGCUT (12.0-20.0)		: 1478
Rerr REF. MAGERR CUT < 0.05		: 1478
MAGERR_APER_2 CUT < 0.05		: 947
TOTAL #					: 845
MAG TYP     : MAG_APER_2
ZP          = 25.986
ZP ERR      = 0.041
STD.NUMB    = 739
REJ.NUMB    = 106
CLIP UPPER  = 61
CTIP LOWER  = 45
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_3 [5/7]
--------------------------------------------------
ALL					: 1478
--------------------------------------------------
FLAG(<=2)				: 1349
R REF. MAGCUT (12.0-20.0)		: 1478
Rerr REF. MAGERR CUT < 0.05		: 1478
MAGERR_APER_3 CUT < 0.05		: 821
TOTAL #					: 732
MAG TYP     : MAG_APER_3
ZP          = 

#	Image subtraction


In [24]:
print('IMAGE SUBTRACTION')
subtracted_images = []
ds9comlist = []
for inim in combined_images:
	hdr = fits.getheader(inim)
	# obs = os.path.basename(inim).split('-')[1]
	# obs = 'LOAO'
	obj = hdr['object']
	filte = hdr['filter']
	path_refim = '/data3/paek/factory/ref_frames/{}'.format(obs)
	refimlist = glob.glob('{}/Ref*{}*{}*.fits'.format(path_refim, obj, filte))
	if len(refimlist) > 0:
		refim = refimlist[0]

		# subim, ds9com = tool.subtraction_routine3(inim, refim)

		# if False:
		if obs not in ['LSGT', 'DOAO', 'RASA36', 'SAO_C361K',]:
			subim, ds9com = tool.subtraction_routine(inim, refim)
		else:
			subim, ds9com = tool.subtraction_routine2(inim, refim)
			if os.path.getsize(subim) != 0:
				rmcom = f"rm {subim}"
				print(rmcom)
				os.system(rmcom)
				subim, ds9com = tool.subtraction_routine(inim, refim)
			else:
				pass

		subtracted_images.append(subim)
		ds9comlist.append(ds9com)
	else:
		print('There is no reference image for {}'.format(os.path.basename(inim)))
		pass
rmcom = 'rm {}/*Ref*gregister.fits'.format(path_data)
print(rmcom)
os.system(rmcom)
# tdict['subtraction'] = time.time() - st - tdict[list(tdict.keys())[-1]]
protbl['status'][protbl['process']=='subtraction'] = True
protbl['time'][protbl['process']=='subtraction'] = int(time.time() - st_)

IMAGE SUBTRACTION
##########  Preparing reference ...
No filter file found, using default filter
No NNW file found, using default NNW config


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:42:56 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC5668-20230421-112526-B-180.com.fits
----- Measuring from: Calib-LOAO-NGC5668-20230421-112526-B-180.com.fits
      "NGC5668" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896

Number of sources in catalog : 212
EXT_NUMBER values found in catalog : 1
I've selected 199 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  199 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
########## Processing /data3/paek/factory/ref_frames/LOAO/Ref-LOAO-NGC5668-0-0-B-0.fits
No filter file found, using default filter
No NNW file found, using default NNW config


> Initializing catalog
> Looking for Ref-LOAO-NGC5668-0-0-B-0.fits
----- Measuring from: Ref-LOAO-NGC5668-0-0-B-0.fits
      "NGC5668" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting up background map at line:  960
> Setting up background map at line: 1024
> Setting up background map at line: 1088
> Setting up background map at line: 1152
> S

Number of sources in catalog : 327
EXT_NUMBER values found in catalog : 1
I've selected 262 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  262 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00015236) : Rotation   +0.133650 [deg], scale 0.999634
Cand  2 (dist.   0.00038894) : Rotation   +0.158322 [deg], scale 0.999489
Cand  3 (dist.   0.00039885) : Rotation   +0.133650 [deg], scale 0.999634
Cand  4 (dist.   0.00040266) : Rotation   +0.133650 [deg], scale 0.999634
195/262 stars with distance < r = 5.0 (mean 0.3, median 0.2, std 0.2)
Filtered for companions, keeping 195/195 matches
Refitting transform (before/after) :
Rotation   +0.133650 [deg], scale 0.999634
Rotation   +0.139842 [deg], scale 0.999778
195/262 stars with distance < r = 5.0 (mean 0.2, median 0.2, std 0.2)
Filtered for companions, keeping 195/195 matches
I'm done !
Computed flux ratio from 

...

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:45:37 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Ref-LOAO-NGC6814-0-0-R-0.fits
----- Measuring from: Ref-LOAO-NGC6814-0-0-R-0.fits
      "NGC6814" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting up background map at line:  9

Number of sources in catalog : 5621
EXT_NUMBER values found in catalog : 1
I've selected 5524 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00028334) : Rotation   +0.241142 [deg], scale 1.001604
Cand  2 (dist.   0.00033949) : Rotation   +0.255239 [deg], scale 1.001353
Cand  3 (dist.   0.00035496) : Rotation   +0.241142 [deg], scale 1.001604
Cand  4 (dist.   0.00035724) : Rotation   +0.241142 [deg], scale 1.001604
480/500 stars with distance < r = 5.0 (mean 0.3, median 0.2, std 0.3)
Filtered for companions, keeping 479/480 matches
Refitting transform (before/after) :
Rotation   +0.241142 [deg], scale 1.001604
Rotation   +0.244955 [deg], scale 1.001491
480/500 stars with distance < r = 5.0 (mean 0.2, median 0.1, std 0.3)
Filtered for companions, keeping 479/480 matches
I'm done !
Computed flux ratio fro

Doing : /data4/gecko/factory/loao/2023_0420/Calib-LOAO-NGC6814-20230421-115833-R-180.com.fits -
        /data4/gecko/factory/loao/2023_0420/Ref-LOAO-NGC6814-0-0-R-0_gregister.fits =
        /data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC6814-20230421-115833-R-180.com.fits
   Good templ data : -100000.0 -> 6000000000.0
   Good image data : -100000.0 -> 60000.0
Mallocing massive amounts of memory...
Region 0 pixels            : 1:2048,1:2048
 Vector Indices (buffered) : 0:2047,0:2047
 Vector Indices (good data): 0:2047,0:2047
Build stamp  : t    0 i    0 (grid coord  0  0)
Build stamp  : t    1 i    0 (grid coord  1  0)
Build stamp  : t    2 i    0 (grid coord  2  0)
Build stamp  : t    3 i    0 (grid coord  3  0)
Build stamp  : t    4 i    0 (grid coord  4  0)
Build stamp  : t    5 i    0 (grid coord  5  0)
Build stamp  : t    6 i    0 (grid coord  6  0)
Build stamp  : t    7 i    0 (grid coord  7  0)
Build stamp  : t    8 i    0 (grid coord  8  0)
Build stamp  : t    9 i    0 (gri

rm /data4/gecko/factory/loao/2023_0420/*Ref*gregister.fits


   Mean   : 0.00
   Median : 0.00
   Mode   : 0.00
   Stdev  : 10000000000.00
 Emperical / Expected Noise for OK pixels = inf

Region 0 finished

SUCCESS


##	Photometry for subtracted images


In [25]:
st_ = time.time()
#	Write photometry configuration
s = open(path_new_gphot, 'w')
for line in lines:
	if 'imkey' in line:
		# line = '{}\t{}/hd*com.fits'.format('imkey', path_data)
		line = '{}\t{}/hd*.fits'.format('imkey', path_data)
	else:
		pass
	if 'photfraction' in line:
		line = '{}\t{}'.format('photfraction', 1.0)
	else:
		pass
	if 'DETECT_MINAREA' in line:
		line = '{}\t{}'.format('DETECT_MINAREA', 10)
	else:
		pass
	if 'DETECT_THRESH' in line:
		line = '{}\t{}'.format('DETECT_THRESH', 1.25)
	else:
		pass
	s.write(line+'\n')
s.close()
#	Execute
hdimlist = sorted(glob.glob('{}/hd*.fits'.format(path_data)))
if len(hdimlist) > 0:
	com = 'python {} {}'.format(path_phot_sub, path_data)
	print(com)
	os.system(com)
	# tdict['photometry_sub'] = time.time() - st - tdict[list(tdict.keys())[-1]]
else:
	print('No subtracted image.')
	pass
protbl['status'][protbl['process']=='photometry_sub'] = True
protbl['time'][protbl['process']=='photometry_sub'] = int(time.time() - st_)

python ./phot/gregoryphot_sub_2021.py /data4/gecko/factory/loao/2023_0420
/data4/gecko/factory/loao/2023_0420/gphot.config
No transient catalog for photometry
#	14 images to do photometry
0	/data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC5668-20230421-112526-B-180.com.fits
1	/data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC5668-20230421-112819-R-180.com.fits
2	/data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC5850-20230421-111355-B-180.com.fits
3	/data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC5850-20230421-111814-R-180.com.fits
4	/data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC5962-20230421-110224-B-180.com.fits
5	/data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC5962-20230421-110614-R-180.com.fits
6	/data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC6070-20230421-113404-B-180.com.fits
7	/data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC6070-20230421-113824-R-180.com.fits
8	/data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC6090-20230421-105052-B-180.com.fits
9	

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:45:52 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing check-image(s)
> Initializing catalog
> Looking for hdCalib-LOAO-NGC5668-20230421-112526-B-180.com.fits
----- Measuring from: hdCalib-LOAO-NGC5668-20230421-112526-B-180.com.fits
      "NGC5668" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map 

ZERO POINT CALCULATION for MAG_AUTO
ZERO POINT CALCULATION for MAG_APER
ZERO POINT CALCULATION for MAG_APER_1
ZERO POINT CALCULATION for MAG_APER_2
ZERO POINT CALCULATION for MAG_APER_3
ZERO POINT CALCULATION for MAG_APER_4
ZERO POINT CALCULATION for MAG_APER_5
------------------------------------------------------------
[2/14] /data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC5668-20230421-112819-R-180.com.fits
LOAO	NGC5668 in R-band
------------------------------------------------------------
2. SOURCE EXTRACTOR
sex -c /home/paek/config/gregoryphot.sex /data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC5668-20230421-112819-R-180.com.fits -CATALOG_NAME /data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC5668-20230421-112819-R-180.com.cat -CATALOG_TYPE ASCII_HEAD -PARAMETERS_NAME /home/paek/config/gregoryphot.param -DETECT_TYPE CCD -DETECT_MINAREA 10 -DETECT_MAXAREA 0 -DETECT_THRESH 1.25 -ANALYSIS_THRESH 1.5 -FILTER Y -FILTER_NAME /home/paek/config/gregoryphot.conv -DEBLEND_NTHRESH 

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:45:53 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing check-image(s)
> Initializing catalog
> Looking for hdCalib-LOAO-NGC5668-20230421-112819-R-180.com.fits
----- Measuring from: hdCalib-LOAO-NGC5668-20230421-112819-R-180.com.fits
      "NGC5668" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map 

ZERO POINT CALCULATION for MAG_AUTO
ZERO POINT CALCULATION for MAG_APER
ZERO POINT CALCULATION for MAG_APER_1
ZERO POINT CALCULATION for MAG_APER_2
ZERO POINT CALCULATION for MAG_APER_3
ZERO POINT CALCULATION for MAG_APER_4
ZERO POINT CALCULATION for MAG_APER_5
------------------------------------------------------------
[3/14] /data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC5850-20230421-111355-B-180.com.fits
LOAO	NGC5850 in B-band
------------------------------------------------------------
2. SOURCE EXTRACTOR
sex -c /home/paek/config/gregoryphot.sex /data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC5850-20230421-111355-B-180.com.fits -CATALOG_NAME /data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC5850-20230421-111355-B-180.com.cat -CATALOG_TYPE ASCII_HEAD -PARAMETERS_NAME /home/paek/config/gregoryphot.param -DETECT_TYPE CCD -DETECT_MINAREA 10 -DETECT_MAXAREA 0 -DETECT_THRESH 1.25 -ANALYSIS_THRESH 1.5 -FILTER Y -FILTER_NAME /home/paek/config/gregoryphot.conv -DEBLEND_NTHRESH 

...

ZERO POINT CALCULATION for MAG_AUTO
ZERO POINT CALCULATION for MAG_APER
ZERO POINT CALCULATION for MAG_APER_1
ZERO POINT CALCULATION for MAG_APER_2
ZERO POINT CALCULATION for MAG_APER_3
ZERO POINT CALCULATION for MAG_APER_4
ZERO POINT CALCULATION for MAG_APER_5
------------------------------------------------------------
[13/14] /data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC6814-20230421-115414-B-180.com.fits
LOAO	NGC6814 in B-band
------------------------------------------------------------
2. SOURCE EXTRACTOR
sex -c /home/paek/config/gregoryphot.sex /data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC6814-20230421-115414-B-180.com.fits -CATALOG_NAME /data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC6814-20230421-115414-B-180.com.cat -CATALOG_TYPE ASCII_HEAD -PARAMETERS_NAME /home/paek/config/gregoryphot.param -DETECT_TYPE CCD -DETECT_MINAREA 10 -DETECT_MAXAREA 0 -DETECT_THRESH 1.25 -ANALYSIS_THRESH 1.5 -FILTER Y -FILTER_NAME /home/paek/config/gregoryphot.conv -DEBLEND_NTHRESH

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:46:03 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing check-image(s)
> Initializing catalog
> Looking for hdCalib-LOAO-NGC6814-20230421-115414-B-180.com.fits
----- Measuring from: hdCalib-LOAO-NGC6814-20230421-115414-B-180.com.fits
      "NGC6814" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map 

ZERO POINT CALCULATION for MAG_AUTO
ZERO POINT CALCULATION for MAG_APER
ZERO POINT CALCULATION for MAG_APER_1
ZERO POINT CALCULATION for MAG_APER_2
ZERO POINT CALCULATION for MAG_APER_3
ZERO POINT CALCULATION for MAG_APER_4
ZERO POINT CALCULATION for MAG_APER_5
------------------------------------------------------------
[14/14] /data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC6814-20230421-115833-R-180.com.fits
LOAO	NGC6814 in R-band
------------------------------------------------------------
2. SOURCE EXTRACTOR
sex -c /home/paek/config/gregoryphot.sex /data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC6814-20230421-115833-R-180.com.fits -CATALOG_NAME /data4/gecko/factory/loao/2023_0420/hdCalib-LOAO-NGC6814-20230421-115833-R-180.com.cat -CATALOG_TYPE ASCII_HEAD -PARAMETERS_NAME /home/paek/config/gregoryphot.param -DETECT_TYPE CCD -DETECT_MINAREA 10 -DETECT_MAXAREA 0 -DETECT_THRESH 1.25 -ANALYSIS_THRESH 1.5 -FILTER Y -FILTER_NAME /home/paek/config/gregoryphot.conv -DEBLEND_NTHRESH

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:46:03 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing check-image(s)
> Initializing catalog
> Looking for hdCalib-LOAO-NGC6814-20230421-115833-R-180.com.fits
----- Measuring from: hdCalib-LOAO-NGC6814-20230421-115833-R-180.com.fits
      "NGC6814" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map 

ZERO POINT CALCULATION for MAG_AUTO
ZERO POINT CALCULATION for MAG_APER
ZERO POINT CALCULATION for MAG_APER_1
ZERO POINT CALCULATION for MAG_APER_2
ZERO POINT CALCULATION for MAG_APER_3
ZERO POINT CALCULATION for MAG_APER_4
ZERO POINT CALCULATION for MAG_APER_5
5. RESULT TO FILES
0 failed images
PHOTOMETRY IS DONE.	(11.774 seconds)


##	Transient Search


In [26]:
st_ = time.time()
fovval = fov.value
#	Input table for transient search
tstbl = Table()
# hdimlist = sorted(glob.glob(f'{path_data}/hd*com.fits'))
hdimlist = sorted(glob.glob(f'{path_data}/hd*.fits'))
if len(hdimlist) != 0:
	tstbl['hdim'] = hdimlist
	tskeys = ['hdcat', 'hcim', 'inim', 'scicat', 'refim']
	for key in tskeys:
		tstbl[key] = ' '*300
	tstbl['fovval'] = fovval

	for i, hdim in enumerate(hdimlist):
		hdcat = hdim.replace('.fits','.phot_sub.cat')
		hcim = hdim.replace('hdCalib', 'hcCalib')
		inim = hdim.replace('hdCalib', 'Calib')
		scicat = inim.replace('.fits', '.phot.cat')

		hdr = fits.getheader(hdim)
		obj = hdr['object']
		filte = hdr['filter']
		path_refim = f'/data3/paek/factory/ref_frames/{obs}'
		refimlist = glob.glob(f'{path_refim}/Ref*{obj}*{filte}*.fits')
		refim = refimlist[0]


		for key, im in zip(tskeys, [hdcat, hcim, inim, scicat, refim]):
			tstbl[key][i] = im

	out_tstbl = f'{path_data}/transient_search.txt'
	tstbl.write(out_tstbl, format='ascii.tab', overwrite=True)

	com = f'python {path_find} {out_tstbl} {ncores}'
	print(com)
	subprocess.call(com, shell=True)		


protbl['status'][protbl['process']=='transient_search'] = True
protbl['time'][protbl['process']=='transient_search'] = int(time.time() - st_)

python ./phot/gregoryfind_bulk_mp_2021.py /data4/gecko/factory/loao/2023_0420/transient_search.txt 8
#	Transient Search Process
------------------------------------------------------------
14 images with 8 cores
------------------------------------------------------------
#	Input
------------------------------------------------------------
hdim : hdCalib-LOAO-NGC5850-20230421-111355-B-180.com.fits
hdcat : hdCalib-LOAO-NGC5850-20230421-111355-B-180.com.phot_sub.cat
hcim : hcCalib-LOAO-NGC5850-20230421-111355-B-180.com.fits
scicat : Calib-LOAO-NGC5850-20230421-111355-B-180.com.phot.cat
fovval : 28.1
------------------------------------------------------------
------------------------------------------------------------
#	Input
------------------------------------------------------------
hdim : hdCalib-LOAO-NGC5668-20230421-112526-B-180.com.fits
hdcat : hdCalib-LOAO-NGC5668-20230421-112526-B-180.com.phot_sub.cat
hcim : hcCalib-LOAO-NGC5668-20230421-112526-B-180.com.fits
scicat : Calib-LOA

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:46:07 with 1 thread

> Setting catalog parameters
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 15:46:07 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing catalog
> Initializing catalog
> Looking for invhdCalib-LOAO-NGC5850-20230421-111355-B-180.com.fits
> Looking for invhdCalib-LOAO-NGC5668-20230421-112526-B-180.com.fits
----- Measuring from: invhdCalib-LOAO-NGC5850-20230421-111355-B-180.com.fits
----- Measuring from: invhdCalib-LOAO-NGC5668-20230421-112526-B-180.com.fits
      "NGC5850" / no ext. header / 2048x2048 / 32 bits (floats)
      "NGC5668" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: Detection+Measurement image: > Setting up background maps
> Setting up background maps
> Setting up background map 

sex -c /home/paek/config/transient.sex /data4/gecko/factory/loao/2023_0420/invhcCalib-LOAO-NGC6070-20230421-113404-B-180.com.fits -CATALOG_NAME /data4/gecko/factory/loao/2023_0420/invhcCalib-LOAO-NGC6070-20230421-113404-B-180.com.cat -CATALOG_TYPE ASCII_HEAD -PARAMETERS_NAME /home/paek/config/transient.param -DETECT_TYPE CCD -DETECT_MINAREA 5 -DETECT_MAXAREA 0 -DETECT_THRESH 1.5 -ANALYSIS_THRESH 1.5 -FILTER Y -FILTER_NAME /home/paek/config/transient.conv -DEBLEND_NTHRESH 64 -DEBLEND_MINCONT 0.0001 -CLEAN Y -CLEAN_PARAM 1.0 -MASK_TYPE CORRECT -PHOT_AUTOPARAMS 2.5,3.5 -PHOT_PETROPARAMS 2.0,3.5 -SATUR_LEVEL 65000.0 -SATUR_KEY SQTURATE -MAG_ZEROPOINT 0.0 -MAG_GAMMA 4.0 -GAIN 1.0 -GAIN_KEY GAIN -PIXEL_SCALE 1.0 -SEEING_FWHM 3.125 -STARNNW_NAME /home/paek/config/transient.nnw -BACK_SIZE 128 -BACK_FILTERSIZE 10 -BACKPHOTO_TYPE LOCAL -CHECKIMAGE_TYPE NONE -CHECKIMAGE_NAME check.fits -MEMORY_OBJSTACK 3000 -MEMORY_PIXSTACK 300000 -MEMORY_BUFSIZE 1024 -VERBOSE_TYPE NORMAL -HEADER_SUFFIX .head -WR

> Setting up background map at line:  640
> Line: 1375  Objects:      424 detected /      132 sextracted
> Line: 1200  Objects:      451 detected /       67 sextracted
> Line: 1400  Objects:      409 detected /      104 sextracted
> Setting up background map at line: 1280
> Line: 1225  Objects:      455 detected /       70 sextracted
> Setting up background map at line:  768
> Line: 1425  Objects:      413 detected /      113 sextracted
> Setting up background map at line: 1408
> Line: 1250  Objects:      461 detected /       75 sextracted
> Line: 1450  Objects:      420 detected /      114 sextracted
> Setting up background map at line:  896
> Setting up background map at line: 1536
> Line: 1475  Objects:      426 detected /      118 sextracted
> Setting up background map at line: 1024
> Line: 1400  Objects:      428 detected /      139 sextracted
> Line: 1275  Objects:      468 detected /       83 sextracted
> Line: 1425  Objects:      428 detected /      142 sextracted
> Setting up 

sex -c /home/paek/config/transient.sex /data4/gecko/factory/loao/2023_0420/invhcCalib-LOAO-NGC6070-20230421-113824-R-180.com.fits -CATALOG_NAME /data4/gecko/factory/loao/2023_0420/invhcCalib-LOAO-NGC6070-20230421-113824-R-180.com.cat -CATALOG_TYPE ASCII_HEAD -PARAMETERS_NAME /home/paek/config/transient.param -DETECT_TYPE CCD -DETECT_MINAREA 5 -DETECT_MAXAREA 0 -DETECT_THRESH 1.5 -ANALYSIS_THRESH 1.5 -FILTER Y -FILTER_NAME /home/paek/config/transient.conv -DEBLEND_NTHRESH 64 -DEBLEND_MINCONT 0.0001 -CLEAN Y -CLEAN_PARAM 1.0 -MASK_TYPE CORRECT -PHOT_AUTOPARAMS 2.5,3.5 -PHOT_PETROPARAMS 2.0,3.5 -SATUR_LEVEL 65000.0 -SATUR_KEY SQTURATE -MAG_ZEROPOINT 0.0 -MAG_GAMMA 4.0 -GAIN 1.0 -GAIN_KEY GAIN -PIXEL_SCALE 1.0 -SEEING_FWHM 2.891 -STARNNW_NAME /home/paek/config/transient.nnw -BACK_SIZE 128 -BACK_FILTERSIZE 10 -BACKPHOTO_TYPE LOCAL -CHECKIMAGE_TYPE NONE -CHECKIMAGE_NAME check.fits -MEMORY_OBJSTACK 3000 -MEMORY_PIXSTACK 300000 -MEMORY_BUFSIZE 1024 -VERBOSE_TYPE NORMAL -HEADER_SUFFIX .head -WR

...

sex -c /home/paek/config/transient.sex /data4/gecko/factory/loao/2023_0420/invhcCalib-LOAO-NGC6814-20230421-115833-R-180.com.fits -CATALOG_NAME /data4/gecko/factory/loao/2023_0420/invhcCalib-LOAO-NGC6814-20230421-115833-R-180.com.cat -CATALOG_TYPE ASCII_HEAD -PARAMETERS_NAME /home/paek/config/transient.param -DETECT_TYPE CCD -DETECT_MINAREA 5 -DETECT_MAXAREA 0 -DETECT_THRESH 1.5 -ANALYSIS_THRESH 1.5 -FILTER Y -FILTER_NAME /home/paek/config/transient.conv -DEBLEND_NTHRESH 64 -DEBLEND_MINCONT 0.0001 -CLEAN Y -CLEAN_PARAM 1.0 -MASK_TYPE CORRECT -PHOT_AUTOPARAMS 2.5,3.5 -PHOT_PETROPARAMS 2.0,3.5 -SATUR_LEVEL 65000.0 -SATUR_KEY SQTURATE -MAG_ZEROPOINT 0.0 -MAG_GAMMA 4.0 -GAIN 1.0 -GAIN_KEY GAIN -PIXEL_SCALE 1.0 -SEEING_FWHM 3.232 -STARNNW_NAME /home/paek/config/transient.nnw -BACK_SIZE 128 -BACK_FILTERSIZE 10 -BACKPHOTO_TYPE LOCAL -CHECKIMAGE_TYPE NONE -CHECKIMAGE_NAME check.fits -MEMORY_OBJSTACK 3000 -MEMORY_PIXSTACK 300000 -MEMORY_BUFSIZE 1024 -VERBOSE_TYPE NORMAL -HEADER_SUFFIX .head -WR

> Line:  100  Objects:      234 detected /        0 sextracted
> Line:  125  Objects:      291 detected /        0 sextracted
> Line:  150  Objects:      338 detected /        0 sextracted
> Line:  175  Objects:      392 detected /        0 sextracted
> Line:  200  Objects:      438 detected /        0 sextracted
> Line:  225  Objects:      480 detected /        0 sextracted
> Line:  250  Objects:      522 detected /        0 sextracted
> Line:  275  Objects:      579 detected /        0 sextracted
> Line:  300  Objects:      635 detected /        0 sextracted
> Line:  325  Objects:      695 detected /        0 sextracted
> Line:  350  Objects:      721 detected /        0 sextracted
> Line:  375  Objects:      745 detected /        0 sextracted
> Line:  400  Objects:      760 detected /        0 sextracted
> Line:  425  Objects:      807 detected /        0 sextracted


------------------------------------------------------------
Filtered sources	: 317 91%
Transient Candidates	: 29 8%
#	Snapshot maker (29)


> Line:  450  Objects:      824 detected /        0 sextracted
> Line:  475  Objects:      846 detected /        0 sextracted
> Line:  500  Objects:      860 detected /        0 sextracted
> Line:  525  Objects:      874 detected /        0 sextracted
> Line:  550  Objects:      907 detected /        0 sextracted
> Line:  575  Objects:      944 detected /        0 sextracted
> Line:  600  Objects:     1009 detected /        0 sextracted
> Line:  625  Objects:     1088 detected /        0 sextracted
> Line:  650  Objects:     1128 detected /        0 sextracted
> Line:  675  Objects:     1175 detected /        0 sextracted
> Line:  700  Objects:     1200 detected /        0 sextracted
> Line:  725  Objects:     1221 detected /        0 sextracted
> Line:  750  Objects:     1231 detected /        0 sextracted
> Line:  775  Objects:     1247 detected /        0 sextracted
> Line:  800  Objects:     1282 detected /        0 sextracted
> Line:  825  Objects:     1315 detected /        0 sex

flag==0 : 0 0%
flag==1 : 84 14%
flag==2 : 3 0%
flag==3 : 215 37%
flag==4 : 83 14%
flag==5 : 84 14%
flag==6 : 35 6%
flag==7 : 61 10%
flag==8 : 0 0%
flag==9 : 375 66%
flag==10 : 49 8%
flag==11 : 68 11%
flag==12 : 20 3%
------------------------------------------------------------
Filtered sources	: 479 84%
Transient Candidates	: 89 15%
#	Snapshot maker (89)


#	Summary file

In [27]:
#------------------------------------------------------------
#------------------------------------------------------------
protbl['status'][protbl['process']=='total'] = True
protbl['time'][protbl['process']=='total'] = int(time.time() - st)	
protbl.write('{}/obs.summary.log'.format(path_data), format='ascii.tab', overwrite=True)
print(protbl)
#	Write data summary
f = open(path_data+'/obs.summary.log', 'a')
end_localtime = time.strftime('%Y-%m-%d %H:%M:%S (%Z)', time.localtime())
f.write('Pipelne start\t: {}\n'.format(start_localtime))
f.write('Pipelne end\t: {}\n'.format(end_localtime))
try:
	f.write('='*60+'\n')
	f.write('PATH :{}\n'.format(path))
	f.write('OBJECT NUMBER # :{}\n'.format(len(ic_cal.summary)))
	objkind = sorted(set(ic_cal.summary['object']))
	f.write('OBJECTS # : {}\n'.format(objkind))
	for obj in objkind:
		f.write('-'*60+'\n')
		for filte in list(set(ic_cal.summary['filter'])):
			indx_tmp = ic_cal.files_filtered(filter=filte, object=obj)
			if len(indx_tmp) > 0:
				f.write('{}\t{}\n'.format(obj, filte))
except:
	pass
f.close()

    process      status  time
                          s  
---------------- ------ -----
    master_frame   True 197.0
     pre_process   True  47.0
      astrometry   True  27.0
      cr_removal   True  55.0
        defringe   True   0.0
      photometry   True  86.0
     image_stack   True  58.0
  photometry_com   True  44.0
     subtraction   True 224.0
  photometry_sub   True  13.0
transient_search   True 150.0
           total   True 878.0


## File Transfer

In [28]:
rmcom = 'rm {}/inv*.*'.format(path_data, path_data)
print(rmcom)
os.system(rmcom)
tails = ['.transients.', '.new.', '.ref.', '.sub.', '']
for obj in objlist:
	for filte in filterlist:
		for tail in tails:
			# tail = 'transients'
			# obj = 'NGC3147'
			# filte = 'B'

			pathto = f'{path_gal}/{obj}/{obs}/{filte}'
			files = f'{path_data}/*Calib*-{obj}-*-{filte}-*{tail}*'
			nfiles = len(glob.glob(files))
			# print(files, nfiles)
			# if nfiles >0:
			# 	print(obj, filte, pathto, files, glob.glob(files)[-1])
			if nfiles !=0:
				#	Save path
				if tail == '':
					pathto = f'{path_gal}/{obj}/{obs}/{filte}'
				else:
					pathto = f'{path_gal}/{obj}/{obs}/{filte}/transients'
				#	Make path
				if (not os.path.exists(pathto)):
					os.makedirs(pathto)
				mvcom = f'mv {files} {pathto}'
				print(mvcom)
				os.system(mvcom)
#	Image transfer
mvcom = f'mv {path_data} {path_save}'
os.system(mvcom)
#	WRITE LOG
f = open(path_log, 'a')
# f.write(path_raw+'/'+os.path.basename(path_data)+'\n')
# f.write('{}/{}\n'.format(path_raw, os.path.basename(path_data)))
f.write(f'{path_raw}/{os.path.basename(path_data)}\n')
f.close()

rm /data4/gecko/factory/loao/2023_0420/inv*.*
mv /data4/gecko/factory/loao/2023_0420/*Calib*-NGC5668-*-B-*.transients.* /data6/IMSNG/IMSNGgalaxies/NGC5668/LOAO/B/transients
mv /data4/gecko/factory/loao/2023_0420/*Calib*-NGC5668-*-B-*.new.* /data6/IMSNG/IMSNGgalaxies/NGC5668/LOAO/B/transients
mv /data4/gecko/factory/loao/2023_0420/*Calib*-NGC5668-*-B-*.ref.* /data6/IMSNG/IMSNGgalaxies/NGC5668/LOAO/B/transients
mv /data4/gecko/factory/loao/2023_0420/*Calib*-NGC5668-*-B-*.sub.* /data6/IMSNG/IMSNGgalaxies/NGC5668/LOAO/B/transients
mv /data4/gecko/factory/loao/2023_0420/*Calib*-NGC5668-*-B-** /data6/IMSNG/IMSNGgalaxies/NGC5668/LOAO/B
mv /data4/gecko/factory/loao/2023_0420/*Calib*-NGC5668-*-R-*.transients.* /data6/IMSNG/IMSNGgalaxies/NGC5668/LOAO/R/transients
mv /data4/gecko/factory/loao/2023_0420/*Calib*-NGC5668-*-R-*.new.* /data6/IMSNG/IMSNGgalaxies/NGC5668/LOAO/R/transients
mv /data4/gecko/factory/loao/2023_0420/*Calib*-NGC5668-*-R-*.ref.* /data6/IMSNG/IMSNGgalaxies/NGC5668/LOAO/R/transie

##	Slack message

In [29]:
total_time = round(protbl['time'][protbl['process']=='total'].item()/60., 1)

channel = '#pipeline'
text = f'[`gpPy`/{project}-{obsmode}] Processing Complete {obs} {os.path.basename(path)} Data ({nobj} objects) with {ncores} cores taking {total_time} mins'

param_slack = dict(
	token = OAuth_Token,
	channel = channel,
	text = text,
)

tool.slack_bot(**param_slack)

<Response [200]>
